In [1]:
import pandas as pd
class KaasAPIConfig:
    def __init__(self):
        self.auth_url = 'https://css.api.hp.com/oauth/accesstoken'
        self.auth_client_id = 'oVKELXf84JwfA1YKnAAAMt15mPs8T1BW'          
        self.auth_client_secret = 'FGU4NRkV9GmCNIWuL3P7LITu5Jt7Tgg5' #'byf9T3wXXcCljGKcPAWxs9sxow4EAA2J'
        self.api_base_url = 'https://css.api.hp.com/knowledge/v2/search'  
        self.api_result_limit = '1000'
        self.domain_map = self.load_domain_map_from_csv()
    
    def get_print_fields(self):
        return (
            'documentID,title,contenttypeheader,product,contenttype,contentupdatedate,'
            'languagecode,disclosurelevel,store,description,renderlink,ishType,'
            'technicalLevel,productstagged,hpid'
        )
        
    def getlookup(self):
        df = pd.read_csv('lookup.csv')
        df['id'] = df['id'].astype(str)
        lookup_dict = dict(zip(df['id'], df['name']))
        return lookup_dict
        
    @staticmethod
    def load_domain_map_from_csv():
        # Read the CSV file into a DataFrame and ensure IDs are read as strings
        df = pd.read_csv('kaas_domain_map.csv', dtype={'product_id': str})
        # Convert the DataFrame back to a dictionary
        domain_map = dict(zip(df['product_id'], df['domain']))
        return domain_map
        
    def get_domain_for_product(self,product_id):
        return self.domain_map.get(str(product_id), None)
    
class OpenSearchConnectConfig:
    def __init__(self):
        self.host = 'vpc-kcs-isearch-wao6ffx5mlzga2q2heyie7jigu.us-west-2.es.amazonaws.com'       
        self.port = 443
        self.auth = ('kcs-admin', '!QAZ2wsx')    
        self.use_ssl = True
        self.verify_certs = False

class SMTPEmailConfig:
    def __init__(self):
        self.sender_email='b-pavan.kumar@hp.com'
        self.receiver_email='neha.prasad@hp.com'
        self.smtp='smtp3.hp.com'
        
class OpenSearchConnectConfigDev:
    def __init__(self):
        self.host = 'vpc-ks-dev-opensearch-es-oacgyoijjstnydxq2itjbftyvm.us-west-2.es.amazonaws.com' 
       # https://vpc-ks-dev-opensearch-es-oacgyoijjstnydxq2itjbftyvm.us-west-2.es.amazonaws.com/
        self.port = 443
        self.auth = ('ks-stg-admin', 'K3!0dg_7Hc')    
        self.use_ssl = True
        self.verify_certs = False
        
class OpenSearchConnectConfigStg:
    def __init__(self):
        self.host = 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com' 
       # https://vpc-ks-dev-opensearch-es-oacgyoijjstnydxq2itjbftyvm.us-west-2.es.amazonaws.com/
        self.port = 443
        self.auth = ('ks-stg-admin', 'K3!0dg_7Hc')    
        self.use_ssl = True
        self.verify_certs = False

In [2]:
from opensearchpy import OpenSearch
from opensearchpy.helpers import bulk
from opensearch_dsl import Search
import requests
import json
import re
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [10]:
   # def getlookup(self):
    #    df = pd.read_csv('lookup.csv')
   #     df['id'] = df['id'].astype(str)
    #    lookup_dict = dict(zip(df['id'], df['name']))
        
    #    return lookup_dict
  #  def get_domain_for_product(self,product_id):
    
    #    df = pd.read_csv('kaas_domain_map.csv')
     #   df['product_id'] = df['product_id'].astype(str)
     #   domain_map = dict(zip(df['product_id'], df['domain']))
        
    #    return domain_map.get(str(product_id), None)
   # def getlookup(self):
   #     return {'90545': 'HP Indigo 1000 Digital Press series', '90547': 'HP Indigo 1000 Digital Press series', '90549': 'HP Indigo 1000 Digital Press series', '3544544': 'HP Indigo 1000 Digital Press series', '3544546': 'HP Indigo 1000 Digital Press series', '2101097052': 'HP Indigo 1000 Digital Press series', '5251493': 'HP Indigo 1000 Digital Press series', '5251494': 'HP Indigo 10000 Digital Press', '2100719849': 'HP Indigo 10000 Digital Press', '2100537754': 'HP Indigo 10000 Digital Press', '2100126517': 'HP Indigo 10000 Digital Press', '2100126528': 'HP Indigo 10000 Digital Press', '5251495': 'HP Indigo 10000 Digital Press', '5251497': 'HP Indigo 10000 Digital Press', '2100126518': 'HP Indigo 10000 Digital Press', '2100126529': 'HP Indigo 10000 Digital Press', '34688149': 'HP Indigo 10000 Digital Press', '34688150': 'HP Indigo 100K Digital Press', '34688151': 'HP Indigo 100K Digital Press', '34688154': 'HP Indigo 100K Digital Press', '35878165': 'HP Indigo 100K Digital Press', '10799634': 'HP Indigo 100K Digital Press', '10799635': 'HP Indigo 12000 Digital Press', '2100719850': 'HP Indigo 12000 Digital Press', '2100537735': 'HP Indigo 12000 Digital Press', '10799636': 'HP Indigo 12000 Digital Press', '10902891': 'HP Indigo 12000 Digital Press', '2100537734': 'HP Indigo 12000 Digital Press', '20945895': 'HP Indigo 12000HD Digital Press', '20945896': 'HP Indigo 12000HD Digital Press', '20945899': 'HP Indigo 12000HD Digital Press', '34688174': 'HP Indigo 12000HD Digital Press', '34688218': 'HP Indigo 15K Digital Press', '34688219': 'HP Indigo 15K Digital Press', '34688222': 'HP Indigo 15K Digital Press', '35865637': 'HP Indigo 15K Digital Press', '35865638': 'HP Indigo 15K Digital Press', '35900353': 'HP Indigo 15K Digital Press', '35865640': 'HP Indigo 15K Digital Press', '3648450': 'HP Indigo 15K Digital Press', '90556': 'HP Indigo s2000 Digital Press', '90558': 'HP Indigo s2000 Digital Press', '90548': 'HP Indigo s2000 Digital Press', '90560': 'HP Indigo s2000 Digital Press', '90559': 'HP Indigo s2000 Digital Press', '3648449': 'HP Indigo ws2000 Digital Press', '90562': 'HP Indigo ws2000 Digital Press', '90564': 'HP Indigo ws2000 Digital Press', '90563': 'HP Indigo ws2000 Digital Press', '5251498': 'HP Indigo ws2000 Digital Press', '5251499': 'HP Indigo 20000 Digital Press', '2100126520': 'HP Indigo 20000 Digital Press', '2100126531': 'HP Indigo 20000 Digital Press', '2100126519': 'HP Indigo 20000 Digital Press', '2100126530': 'HP Indigo 20000 Digital Press', '5251500': 'HP Indigo 20000 Digital Press', '5251502': 'HP Indigo 20000 Digital Press', '37933302': 'HP Indigo 20000 Digital Press', '37933303': 'HP Indigo 25K Digital Press', '34688163': 'HP Indigo 25K Digital Press', '34688166': 'HP Indigo 25K Digital Press', '90565': 'HP Indigo 25K Digital Press', '3640220': 'HP Indigo 3000 Digital Press Series', '2100126557': 'HP Indigo 3000 Digital Press Series', '2100126572': 'HP Indigo 3000 Digital Press Series', '2100126556': 'HP Indigo 3000 Digital Press Series', '2100126571': 'HP Indigo 3000 Digital Press Series', '90568': 'HP Indigo 3000 Digital Press Series', '90570': 'HP Indigo 3000 Digital Press Series', '90569': 'HP Indigo 3000 Digital Press Series', '439129': 'HP Indigo 3000 Digital Press Series', '439130': 'HP Indigo 3000 Digital Press Series', '3382251': 'HP Indigo 3500 Digital Press', '3382252': 'HP Indigo 3500 Digital Press', '3382253': 'HP Indigo 3500 Digital Press', '2101097056': 'HP Indigo 3500 Digital Press', '90566': 'HP Indigo w3200 Digital Press Series', '90573': 'HP Indigo w3200 Digital Press Series', '3218087': 'HP Indigo w3200 Digital Press Series', '90575': 'HP Indigo w3200 Digital Press Series', '3223340': 'HP Indigo w3200 Digital Press Series', '3659874': 'HP Indigo w3250 Digital Press', '3244122': 'HP Indigo w3250 Digital Press', '2100126505': 'HP Indigo w3250 Digital Press', '90574': 'HP Indigo w3250 Digital Press', '5251504': 'HP Indigo w3250 Digital Press', '5251518': 'HP Indigo 30000 Digital Press', '2100126521': 'HP Indigo 30000 Digital Press', '2100126532': 'HP Indigo 30000 Digital Press', '5251533': 'HP Indigo 30000 Digital Press', '5251558': 'HP Indigo 30000 Digital Press', '4214301': 'HP Indigo 30000 Digital Press', '4214302': 'HP Indigo 3550 Digital Press', '2100126512': 'HP Indigo 3550 Digital Press', '2100126524': 'HP Indigo 3550 Digital Press', '4214310': 'HP Indigo 3550 Digital Press', '4214316': 'HP Indigo 3550 Digital Press', '37933299': 'HP Indigo 3550 Digital Press', '34688157': 'HP Indigo 35K Digital Press', '34688158': 'HP Indigo 35K Digital Press', '34702965': 'HP Indigo 35K Digital Press', '35865641': 'HP Indigo 35K Digital Press', '8954213': 'HP Indigo 35K Digital Press', '8954214': 'HP Indigo 3600 Digital Press', '8954215': 'HP Indigo 3600 Digital Press', '8693693': 'HP Indigo 3600 Digital Press', '3648452': 'HP Indigo 3600 Digital Press', '3648451': 'HP Indigo ws4000 Digital Press Series', '90705': 'HP Indigo ws4000 Digital Press Series', '90707': 'HP Indigo ws4000 Digital Press Series', '90706': 'HP Indigo ws4000 Digital Press Series', '438409': 'HP Indigo ws4000 Digital Press Series', '7826422': 'HP Indigo ws4000 Digital Press Series', '7826423': 'HP Indigo ws4000 Digital Press Series', '438413': 'HP Indigo ws4000 Digital Press Series', '7826424': 'HP Indigo ws4000 Digital Press Series', '7826426': 'HP Indigo ws4000 Digital Press Series', '7826427': 'HP Indigo ws4000 Digital Press Series', '7826429': 'HP Indigo ws4000 Digital Press Series', '3252083': 'HP Indigo ws4500 Digital Press', '3252084': 'HP Indigo ws4500 Digital Press', '3252085': 'HP Indigo ws4500 Digital Press', '2100126507': 'HP Indigo ws4500 Digital Press', '2101097041': 'HP Indigo ws4500 Digital Press', '3648459': 'HP Indigo ws4500 Digital Press', '383572': 'HP Indigo 5000 Digital Press series', '2100126558': 'HP Indigo 5000 Digital Press series', '2100126573': 'HP Indigo 5000 Digital Press series', '5338467': 'HP Indigo 5000 Digital Press series', '5338468': 'HP Indigo 5000 Digital Press series', '383574': 'HP Indigo 5000 Digital Press series', '5350520': 'HP Indigo 5000 Digital Press series', '383575': 'HP Indigo 5000 Digital Press series', '3382246': 'HP Indigo 5500 Digital Press', '3382247': 'HP Indigo 5500 Digital Press', '3382249': 'HP Indigo 5500 Digital Press', '2101097028': 'HP Indigo 5500 Digital Press', '10902899': 'HP Indigo 5500 Digital Press', '10902900': 'HP Indigo 50000 Digital Press', '10902901': 'HP Indigo 50000 Digital Press', '10902904': 'HP Indigo 50000 Digital Press', '5226271': 'HP Indigo 50000 Digital Press', '5226272': 'HP Indigo 5600 Digital Press', '5226273': 'HP Indigo 5600 Digital Press', '5226275': 'HP Indigo 5600 Digital Press', '2100126513': 'HP Indigo 5600 Digital Press', '10799727': 'HP Indigo 5600 Digital Press', '10799728': 'HP Indigo 5900 Digital Press', '10799729': 'HP Indigo 5900 Digital Press', '10799732': 'HP Indigo 5900 Digital Press', '10902893': 'HP Indigo 5900 Digital Press', '10902894': 'HP Indigo 5r Digital Press', '10902895': 'HP Indigo 5r Digital Press', '10902898': 'HP Indigo 5r Digital Press', '18021216': 'HP Indigo 5r Digital Press', '18021217': 'HP Indigo 6900 Digital Press', '2100719846': 'HP Indigo 6900 Digital Press', '2100537703': 'HP Indigo 6900 Digital Press', '18021218': 'HP Indigo 6900 Digital Press', '18021221': 'HP Indigo 6900 Digital Press', '37933300': 'HP Indigo 6900 Digital Press', '37933301': 'HP Indigo 6K Digital Press', '34766689': 'HP Indigo 6K Digital Press', '34766692': 'HP Indigo 6K Digital Press', '2101341287': 'HP Indigo 6K Digital Press', '2101341290': 'HP Indigo 6K Secure Digital Press series', '2101341301': 'HP Indigo 6K Secure Digital Press series', '2101341317': 'HP Indigo 6K Secure Digital Press series', '10902906': 'HP Indigo 6K Secure Digital Press series', '10902907': 'HP Indigo 6r Digital Press', '10902908': 'HP Indigo 6r Digital Press', '10902910': 'HP Indigo 6r Digital Press', '3722855': 'HP Indigo 6r Digital Press', '3722856': 'HP Indigo 7000 Digital Press series', '2100126514': 'HP Indigo 7000 Digital Press series', '2100126525': 'HP Indigo 7000 Digital Press series', '3722857': 'HP Indigo 7000 Digital Press series', '3722859': 'HP Indigo 7000 Digital Press series', '2101097032': 'HP Indigo 7000 Digital Press series', '5350521': 'HP Indigo 7000 Digital Press series', '4169552': 'HP Indigo 7000 Digital Press series', '4169553': 'HP Indigo 7500 Digital Press', '4169661': 'HP Indigo 7500 Digital Press', '4169663': 'HP Indigo 7500 Digital Press', '5350522': 'HP Indigo 7500 Digital Press', '5226276': 'HP Indigo 7500 Digital Press', '5226277': 'HP Indigo 7600 Digital Press', '2100126515': 'HP Indigo 7600 Digital Press', '2100126526': 'HP Indigo 7600 Digital Press', '5226278': 'HP Indigo 7600 Digital Press', '5226280': 'HP Indigo 7600 Digital Press', '7186479': 'HP Indigo 7600 Digital Press', '7186480': 'HP Indigo 7800 Digital Press', '2100719847': 'HP Indigo 7800 Digital Press', '2100537675': 'HP Indigo 7800 Digital Press', '7186482': 'HP Indigo 7800 Digital Press', '7186484': 'HP Indigo 7800 Digital Press', '2100537674': 'HP Indigo 7800 Digital Press', '10799721': 'HP Indigo 7800 Digital Press', '10799722': 'HP Indigo 7900 Digital Press', '2100719848': 'HP Indigo 7900 Digital Press', '2100537696': 'HP Indigo 7900 Digital Press', '10799723': 'HP Indigo 7900 Digital Press', '10799726': 'HP Indigo 7900 Digital Press', '37933149': 'HP Indigo 7900 Digital Press', '37933150': 'HP Indigo 7K Digital Press', '34702961': 'HP Indigo 7K Digital Press', '34702964': 'HP Indigo 7K Digital Press', '11503597': 'HP Indigo 7K Digital Press', '11503704': 'HP Indigo 7r Digital Press', '11503705': 'HP Indigo 7r Digital Press', '11534765': 'HP Indigo 7r Digital Press', '10799628': 'HP Indigo 7r Digital Press', '10799629': 'HP Indigo 8000 Digital Press', '10799630': 'HP Indigo 8000 Digital Press', '10799633': 'HP Indigo 8000 Digital Press', '37910237': 'HP Indigo 8000 Digital Press', '37910238': 'HP Indigo 8K Digital Press', '37921124': 'HP Indigo 8K Digital Press', '37921126': 'HP Indigo 8K Digital Press', '20540618': 'HP Indigo 8K Digital Press', '20540619': 'HP Indigo GEM Digital Press series', '20540620': 'HP Indigo GEM Digital Press series', '20540624': 'HP Indigo GEM Digital Press series', '33990674': 'HP Indigo GEM Digital Press series', '33990675': 'HP Indigo Kedem Digital Press series', '33990677': 'HP Indigo Kedem Digital Press series', '33990680': 'HP Indigo Kedem Digital Press series', '2101480396': 'HP Indigo Kedem Digital Press series', '2101480397': 'HP Indigo V12 Digital Press', '2101480398': 'HP Indigo V12 Digital Press', '2101480399': 'HP Indigo V12 Digital Press', '3919426': 'HP Indigo V12 Digital Press', '3919427': 'HP Indigo W7200 Digital Press', '3919429': 'HP Indigo W7200 Digital Press', '3919431': 'HP Indigo W7200 Digital Press', '2100537651': 'HP Indigo W7200 Digital Press', '5251478': 'HP Indigo W7200 Digital Press', '5251479': 'HP Indigo W7250 Digital Press', '2100126516': 'HP Indigo W7250 Digital Press', '2100126527': 'HP Indigo W7250 Digital Press', '5251480': 'HP Indigo W7250 Digital Press', '5251482': 'HP Indigo W7250 Digital Press', '2100537669': 'HP Indigo W7250 Digital Press', '5173002': 'HP Indigo W7250 Digital Press', '5173003': 'HP Indigo WS4600 Digital Press', '5173004': 'HP Indigo WS4600 Digital Press', '5173006': 'HP Indigo WS4600 Digital Press', '3827316': 'HP Indigo WS4600 Digital Press', '3827317': 'HP Indigo WS6000 Digital Press', '3827321': 'HP Indigo WS6000 Digital Press', '3827324': 'HP Indigo WS6000 Digital Press', '2100537647': 'HP Indigo WS6000 Digital Press', '5172997': 'HP Indigo WS6000 Digital Press', '5172998': 'HP Indigo WS6600 Digital Press', '5172999': 'HP Indigo WS6600 Digital Press', '5173001': 'HP Indigo WS6600 Digital Press', '5251488': 'HP Indigo WS6600 Digital Press', '5251489': 'HP Indigo WS6600p Digital Press', '5251490': 'HP Indigo WS6600p Digital Press', '5251492': 'HP Indigo WS6600p Digital Press', '7186486': 'HP Indigo WS6600p Digital Press', '7186487': 'HP Indigo WS6800 Digital Press', '2100719845': 'HP Indigo WS6800 Digital Press', '2100537679': 'HP Indigo WS6800 Digital Press', '7186488': 'HP Indigo WS6800 Digital Press', '7186490': 'HP Indigo WS6800 Digital Press', '10799733': 'HP Indigo WS6800 Digital Press', '10799734': 'HP Indigo WS6800p Digital Press', '10799624': 'HP Indigo WS6800p Digital Press', '10799627': 'HP Indigo WS6800p Digital Press', '3648465': 'HP Indigo WS6800p Digital Press', '90624': 'Indigo Digital Press E-Print Systems', '31592': 'Indigo Digital Press E-Print Systems', '31594': 'Indigo Digital Press E-Print Systems', '90647': 'Indigo Digital Press E-Print Systems', '90648': 'Indigo Digital Press E-Print Systems', '90656': 'Indigo Digital Press E-Print Systems', '90657': 'Indigo Digital Press E-Print Systems', '212612': 'Indigo Digital Press E-Print Systems', '212613': 'Indigo Digital Press E-Print Systems', '212614': 'Indigo Digital Press E-Print Systems', '212615': 'Indigo Digital Press E-Print Systems', '90632': 'Indigo Digital Press E-Print Systems', '90633': 'Indigo Digital Press E-Print Systems', '3648466': 'Indigo Digital Press E-Print Systems', '90680': 'Indigo Digital Press Omnius Systems', '90694': 'Indigo Digital Press Omnius Systems', '90695': 'Indigo Digital Press Omnius Systems', '90682': 'Indigo Digital Press Omnius Systems', '90683': 'Indigo Digital Press Omnius Systems', '3648464': 'Indigo Digital Press Omnius Systems', '90616': 'Indigo Digital Press Ultrastream Systems', '91064': 'Indigo Digital Press Ultrastream Systems', '90571': 'Indigo Digital Press Ultrastream Systems', '2101057694': 'HP PageWide Advantage 2200 Series', '2101057742': 'HP PageWide Advantage 2200 Series', '2101057743': 'HP PageWide Advantage 2200 Series', '2101057744': 'HP PageWide Advantage 2200 Series', '2101571612': 'HP PageWide Advantage 2200 Series', '2100469808': 'HP PageWide Advantage 2200 Series', '2101576959': 'HP PageWide Advantage 2200 Series', '2101587198': 'HP PageWide Advantage 2200 Series', '8961173': 'HP PageWide T1100 Press series', '8961174': 'HP PageWide T1100 Press series', '8961175': 'HP PageWide T1100 Press series', '8961179': 'HP PageWide T1100 Press series', '26355293': 'HP PageWide T1100 Press series', '26355294': 'HP PageWide T1100 Press series', '21399086': 'HP PageWide T1100 Press series', '19530750': 'HP PageWide T1100 Press series', '22810482': 'HP PageWide T1100 Press series', '22810485': 'HP PageWide T1100 Press series', '22810486': 'HP PageWide T1100 Press series', '27789658': 'HP PageWide T1100 Press series', '2100471738': 'HP PageWide T1100 Press series', '2100251354': 'HP PageWide T1100 Press series', '2101236398': 'HP PageWide T1100 Press series', '2101592556': 'HP PageWide T1100 Press series', '2101592554': 'HP PageWide T1100 Press series', '22810488': 'HP PageWide T1100 Press series', '19390976': 'HP PageWide T400S Press', '7477383': 'HP PageWide T400S Press', '7477384': 'HP PageWide T400S Press', '6531107': 'HP PageWide T400S Press', '9119112': 'HP PageWide T400S Press', '2100546245': 'HP PageWide T400S Press', '2100546246': 'HP PageWide T400S Press', '18280253': 'HP PageWide T400S Press', '22757945': 'HP PageWide T400S Press', '2100251355': 'HP PageWide T400S Press', '2100251356': 'HP PageWide T400S Press', '2101581477': 'HP PageWide T700i Press', '2101581485': 'HP PageWide T700i Press', '2101581486': 'HP PageWide T700i Press', '2101581487': 'HP PageWide T700i Press', '4187448': 'HP PageWide Web Press T200 Color series', '4187449': 'HP PageWide Web Press T200 Color series', '4182637': 'HP PageWide Web Press T200 Color series', '5340337': 'HP PageWide Web Press T200 Color series', '5268269': 'HP PageWide Web Press T200 Color series', '5337565': 'HP PageWide Web Press T200 Color series', '6235341': 'HP PageWide Web Press T200 Color series', '4182871': 'HP PageWide Web Press T200 Color series', '5344649': 'HP PageWide Web Press T230 Color series', '5268266': 'HP PageWide Web Press T230 Color series', '2101604811': 'HP PageWide Web Press T230 Color series', '5268268': 'HP PageWide Web Press T230 Color series', '2100543965': 'HP PageWide Web Press T230 Color series', '7153866': 'HP PageWide Web Press T230 Color series', '5351425': 'HP PageWide Web Press T230 Color series', '21399085': 'HP PageWide Web Press T230 Color series', '21331413': 'HP PageWide Web Press T230 Color series', '24269563': 'HP PageWide Web Press T230 Color series', '10903050': 'HP PageWide Web Press T200 HD series', '10903051': 'HP PageWide Web Press T200 HD series', '15594552': 'HP PageWide Web Press T200 HD series', '15594555': 'HP PageWide Web Press T200 HD series', '10903052': 'HP PageWide Web Press T200 HD series', '20562158': 'HP PageWide Web Press T200 HD series', '24229915': 'HP PageWide Web Press T200 HD series', '2100123028': 'HP PageWide Web Press T200 HD series', '10903112': 'HP PageWide Web Press T200 HD series', '19146640': 'HP PageWide Web Press T200 HD series', '2100564222': 'HP PageWide Web Press T200 HD series', '24229916': 'HP PageWide Web Press T200 HD series', '2100564223': 'HP PageWide Web Press T200 HD series', '26256613': 'HP PageWide Web Press T200 HD series', '38111491': 'HP PageWide Web Press T200 HD series', '2100178024': 'HP PageWide Web Press T200 HD series', '2100178025': 'HP PageWide Web Press T200 HD series', '7296800': 'HP PageWide Web Press T200 HD series', '7296801': 'HP PageWide Web Press T260 Mono', '7296803': 'HP PageWide Web Press T260 Mono', '6302739': 'HP PageWide Web Press T260 Mono', '9119106': 'HP PageWide Web Press T260 Mono', '7267178': 'HP PageWide Web Press T260 Mono', '23510688': 'HP PageWide Web Press T260 Mono', '2100124329': 'HP PageWide Web Press T260 Mono', '23510689': 'HP PageWide Web Press T260 Mono', '24381405': 'HP PageWide Web Press T260 Mono', '2100124492': 'HP PageWide Web Press T260 Mono', '3961028': 'HP PageWide Web Press T260 Mono', '13432070': 'HP PageWide Web Press T300 HD series', '13432072': 'HP PageWide Web Press T300 HD series', '13432075': 'HP PageWide Web Press T300 HD series', '13432077': 'HP PageWide Web Press T300 HD series', '13432080': 'HP PageWide Web Press T300 HD series', '13432083': 'HP PageWide Web Press T300 HD series', '13432086': 'HP PageWide Web Press T300 HD series', '13432088': 'HP PageWide Web Press T300 HD series', '13432091': 'HP PageWide Web Press T300 HD series', '5344779': 'HP PageWide Web Press T300 Mono series', '5337539': 'HP PageWide Web Press T300 Mono series', '5337474': 'HP PageWide Web Press T300 Mono series', '5338959': 'HP PageWide Web Press T300 Mono series', '5337542': 'HP PageWide Web Press T300 Mono series', '9119107': 'HP PageWide Web Press T300 Mono series', '3961029': 'HP PageWide Web Press T300 series', '3961030': 'HP PageWide Web Press T300 series', '5337465': 'HP PageWide Web Press T300 series', '5337522': 'HP PageWide Web Press T300 series', '5337533': 'HP PageWide Web Press T300 series', '5337534': 'HP PageWide Web Press T300 series', '2100542946': 'HP PageWide Web Press T300 series', '5337537': 'HP PageWide Web Press T300 series', '2100542947': 'HP PageWide Web Press T300 series', '5337538': 'HP PageWide Web Press T300 series', '5268270': 'HP PageWide Web Press T300 series', '2100542948': 'HP PageWide Web Press T300 series', '5337568': 'HP PageWide Web Press T300 series', '2100124704': 'HP PageWide Web Press T300 series', '5337551': 'HP PageWide Web Press T300 series', '5337554': 'HP PageWide Web Press T300 series', '5337557': 'HP PageWide Web Press T300 series', '2100124705': 'HP PageWide Web Press T300 series', '5337562': 'HP PageWide Web Press T300 series', '5337468': 'HP PageWide Web Press T300 series', '3961032': 'HP PageWide Web Press T300 series', '5337569': 'HP PageWide Web Press T300 series', '5337572': 'HP PageWide Web Press T300 series', '5337575': 'HP PageWide Web Press T300 series', '5096391': 'HP PageWide Web Press T350', '5096393': 'HP PageWide Web Press T350', '5337582': 'HP PageWide Web Press T350', '5337585': 'HP PageWide Web Press T350', '5268280': 'HP PageWide Web Press T350', '5096396': 'HP PageWide Web Press T350', '5344796': 'HP PageWide Web Press T350M', '5337576': 'HP PageWide Web Press T350M', '5337578': 'HP PageWide Web Press T350M', '9119108': 'HP PageWide Web Press T350M', '5344797': 'HP PageWide Web Press T360', '5268272': 'HP PageWide Web Press T360', '5268274': 'HP PageWide Web Press T360', '9119109': 'HP PageWide Web Press T360', '5096372': 'HP PageWide Web Press T360', '5096373': 'HP PageWide Web Press T400 Color series', '5096376': 'HP PageWide Web Press T400 Color series', '5337588': 'HP PageWide Web Press T400 Color series', '5337591': 'HP PageWide Web Press T400 Color series', '5268279': 'HP PageWide Web Press T400 Color series', '5337594': 'HP PageWide Web Press T400 Color series', '24829133': 'HP PageWide Web Press T400 Color series', '5337604': 'HP PageWide Web Press T400 Color series', '5096381': 'HP PageWide Web Press T400 Color series', '5337610': 'HP PageWide Web Press T400 Color series', '5344798': 'HP PageWide Web Press T400 Mono series', '5337595': 'HP PageWide Web Press T400 Mono series', '5337597': 'HP PageWide Web Press T400 Mono series', '5337601': 'HP PageWide Web Press T400 Mono series', '9119110': 'HP PageWide Web Press T400 Mono series', '9119111': 'HP PageWide Web Press T400 Mono series', '9713927': 'HP PageWide Web Press T400 Mono series', '9713929': 'HP PageWide Web Press T400 Mono series', '9713930': 'HP PageWide Web Press T400 Mono series', '5344801': 'HP PageWide Web Press T410', '5268275': 'HP PageWide Web Press T410', '5268278': 'HP PageWide Web Press T410', '5337608': 'HP PageWide Web Press T410', '32613967': 'HP PageWide Web Press T410', '2100543987': 'HP PageWide Web Press T410', '5346844': 'HP PageWide Web Press T410', '8961182': 'HP PageWide Web Press T410', '8961183': 'HP PageWide Web Press T400 HD series', '8961193': 'HP PageWide Web Press T400 HD series', '11145858': 'HP PageWide Web Press T400 HD series', '8961322': 'HP PageWide Web Press T400 HD series', '11145859': 'HP PageWide Web Press T400 HD series', '2100564221': 'HP PageWide Web Press T400 HD series', '2101546336': 'HP PageWide Web Press T400 HD series', '2101546338': 'HP PageWide Web Press T400 HD series', '11145856': 'HP PageWide Web Press T400 HD series', '9068313': 'HP PageWide Web Press T400 HD series', '22757942': 'HP PageWide Web Press T400 HD series', '27789659': 'HP PageWide Web Press T400 HD series', '2101592555': 'HP PageWide Web Press T400 HD series', '11145860': 'HP PageWide Web Press T400 HD series', '9068312': 'HP PageWide Web Press T400 HD series', '34104723': 'HP PageWide Web Press T400 HD series', '2100088957': 'HP PageWide Web Press T400 HD series'}
   # def get_domain_for_product(self,product_id):
   #     domain_map = {'90545': 'Indigo', '90547': 'Indigo', '90549': 'Indigo', '3544544': 'Indigo', '3544546': 'Indigo', '2101097052': 'Indigo', '5251493': 'Indigo', '5251494': 'Indigo', '2100719849': 'Indigo', '2100537754': 'Indigo', '2100126517': 'Indigo', '2100126528': 'Indigo', '5251495': 'Indigo', '5251497': 'Indigo', '2100126518': 'Indigo', '2100126529': 'Indigo', '34688149': 'Indigo', '34688150': 'Indigo', '34688151': 'Indigo', '34688154': 'Indigo', '35878165': 'Indigo', '10799634': 'Indigo', '10799635': 'Indigo', '2100719850': 'Indigo', '2100537735': 'Indigo', '10799636': 'Indigo', '10902891': 'Indigo', '2100537734': 'Indigo', '20945895': 'Indigo', '20945896': 'Indigo', '20945899': 'Indigo', '34688174': 'Indigo', '34688218': 'Indigo', '34688219': 'Indigo', '34688222': 'Indigo', '35865637': 'Indigo', '35865638': 'Indigo', '35900353': 'Indigo', '35865640': 'Indigo', '3648450': 'Indigo', '90556': 'Indigo', '90558': 'Indigo', '90548': 'Indigo', '90560': 'Indigo', '90559': 'Indigo', '3648449': 'Indigo', '90562': 'Indigo', '90564': 'Indigo', '90563': 'Indigo', '5251498': 'Indigo', '5251499': 'Indigo', '2100126520': 'Indigo', '2100126531': 'Indigo', '2100126519': 'Indigo', '2100126530': 'Indigo', '5251500': 'Indigo', '5251502': 'Indigo', '37933302': 'Indigo', '37933303': 'Indigo', '34688163': 'Indigo', '34688166': 'Indigo', '90565': 'Indigo', '3640220': 'Indigo', '2100126557': 'Indigo', '2100126572': 'Indigo', '2100126556': 'Indigo', '2100126571': 'Indigo', '90568': 'Indigo', '90570': 'Indigo', '90569': 'Indigo', '439129': 'Indigo', '439130': 'Indigo', '3382251': 'Indigo', '3382252': 'Indigo', '3382253': 'Indigo', '2101097056': 'Indigo', '90566': 'Indigo', '90573': 'Indigo', '3218087': 'Indigo', '90575': 'Indigo', '3223340': 'Indigo', '3659874': 'Indigo', '3244122': 'Indigo', '2100126505': 'Indigo', '90574': 'Indigo', '5251504': 'Indigo', '5251518': 'Indigo', '2100126521': 'Indigo', '2100126532': 'Indigo', '5251533': 'Indigo', '5251558': 'Indigo', '4214301': 'Indigo', '4214302': 'Indigo', '2100126512': 'Indigo', '2100126524': 'Indigo', '4214310': 'Indigo', '4214316': 'Indigo', '37933299': 'Indigo', '34688157': 'Indigo', '34688158': 'Indigo', '34702965': 'Indigo', '35865641': 'Indigo', '8954213': 'Indigo', '8954214': 'Indigo', '8954215': 'Indigo', '8693693': 'Indigo', '3648452': 'Indigo', '3648451': 'Indigo', '90705': 'Indigo', '90707': 'Indigo', '90706': 'Indigo', '438409': 'Indigo', '7826422': 'Indigo', '7826423': 'Indigo', '438413': 'Indigo', '7826424': 'Indigo', '7826426': 'Indigo', '7826427': 'Indigo', '7826429': 'Indigo', '3252083': 'Indigo', '3252084': 'Indigo', '3252085': 'Indigo', '2100126507': 'Indigo', '2101097041': 'Indigo', '3648459': 'Indigo', '383572': 'Indigo', '2100126558': 'Indigo', '2100126573': 'Indigo', '5338467': 'Indigo', '5338468': 'Indigo', '383574': 'Indigo', '5350520': 'Indigo', '383575': 'Indigo', '3382246': 'Indigo', '3382247': 'Indigo', '3382249': 'Indigo', '2101097028': 'Indigo', '10902899': 'Indigo', '10902900': 'Indigo', '10902901': 'Indigo', '10902904': 'Indigo', '5226271': 'Indigo', '5226272': 'Indigo', '5226273': 'Indigo', '5226275': 'Indigo', '2100126513': 'Indigo', '10799727': 'Indigo', '10799728': 'Indigo', '10799729': 'Indigo', '10799732': 'Indigo', '10902893': 'Indigo', '10902894': 'Indigo', '10902895': 'Indigo', '10902898': 'Indigo', '18021216': 'Indigo', '18021217': 'Indigo', '2100719846': 'Indigo', '2100537703': 'Indigo', '18021218': 'Indigo', '18021221': 'Indigo', '37933300': 'Indigo', '37933301': 'Indigo', '34766689': 'Indigo', '34766692': 'Indigo', '2101341287': 'Indigo', '2101341290': 'Indigo', '2101341301': 'Indigo', '2101341317': 'Indigo', '10902906': 'Indigo', '10902907': 'Indigo', '10902908': 'Indigo', '10902910': 'Indigo', '3722855': 'Indigo', '3722856': 'Indigo', '2100126514': 'Indigo', '2100126525': 'Indigo', '3722857': 'Indigo', '3722859': 'Indigo', '2101097032': 'Indigo', '5350521': 'Indigo', '4169552': 'Indigo', '4169553': 'Indigo', '4169661': 'Indigo', '4169663': 'Indigo', '5350522': 'Indigo', '5226276': 'Indigo', '5226277': 'Indigo', '2100126515': 'Indigo', '2100126526': 'Indigo', '5226278': 'Indigo', '5226280': 'Indigo', '7186479': 'Indigo', '7186480': 'Indigo', '2100719847': 'Indigo', '2100537675': 'Indigo', '7186482': 'Indigo', '7186484': 'Indigo', '2100537674': 'Indigo', '10799721': 'Indigo', '10799722': 'Indigo', '2100719848': 'Indigo', '2100537696': 'Indigo', '10799723': 'Indigo', '10799726': 'Indigo', '37933149': 'Indigo', '37933150': 'Indigo', '34702961': 'Indigo', '34702964': 'Indigo', '11503597': 'Indigo', '11503704': 'Indigo', '11503705': 'Indigo', '11534765': 'Indigo', '10799628': 'Indigo', '10799629': 'Indigo', '10799630': 'Indigo', '10799633': 'Indigo', '37910237': 'Indigo', '37910238': 'Indigo', '37921124': 'Indigo', '37921126': 'Indigo', '20540618': 'Indigo', '20540619': 'Indigo', '20540620': 'Indigo', '20540624': 'Indigo', '33990674': 'Indigo', '33990675': 'Indigo', '33990677': 'Indigo', '33990680': 'Indigo', '2101480396': 'Indigo', '2101480397': 'Indigo', '2101480398': 'Indigo', '2101480399': 'Indigo', '3919426': 'Indigo', '3919427': 'Indigo', '3919429': 'Indigo', '3919431': 'Indigo', '2100537651': 'Indigo', '5251478': 'Indigo', '5251479': 'Indigo', '2100126516': 'Indigo', '2100126527': 'Indigo', '5251480': 'Indigo', '5251482': 'Indigo', '2100537669': 'Indigo', '5173002': 'Indigo', '5173003': 'Indigo', '5173004': 'Indigo', '5173006': 'Indigo', '3827316': 'Indigo', '3827317': 'Indigo', '3827321': 'Indigo', '3827324': 'Indigo', '2100537647': 'Indigo', '5172997': 'Indigo', '5172998': 'Indigo', '5172999': 'Indigo', '5173001': 'Indigo', '5251488': 'Indigo', '5251489': 'Indigo', '5251490': 'Indigo', '5251492': 'Indigo', '7186486': 'Indigo', '7186487': 'Indigo', '2100719845': 'Indigo', '2100537679': 'Indigo', '7186488': 'Indigo', '7186490': 'Indigo', '10799733': 'Indigo', '10799734': 'Indigo', '10799624': 'Indigo', '10799627': 'Indigo', '3648465': 'Indigo', '90624': 'Indigo', '31592': 'Indigo', '31594': 'Indigo', '90647': 'Indigo', '90648': 'Indigo', '90656': 'Indigo', '90657': 'Indigo', '212612': 'Indigo', '212613': 'Indigo', '212614': 'Indigo', '212615': 'Indigo', '90632': 'Indigo', '90633': 'Indigo', '3648466': 'Indigo', '90680': 'Indigo', '90694': 'Indigo', '90695': 'Indigo', '90682': 'Indigo', '90683': 'Indigo', '3648464': 'Indigo', '90616': 'Indigo', '91064': 'Indigo', '90571': 'Indigo', '2101057694': 'PWP', '2101057742': 'PWP', '2101057743': 'PWP', '2101057744': 'PWP', '2101571612': 'PWP', '2100469808': 'PWP', '2101576959': 'PWP', '2101587198': 'PWP', '18576095': 'PWP','8961173': 'PWP', '8961174': 'PWP', '8961175': 'PWP', '8961179': 'PWP', '26355293': 'PWP', '26355294': 'PWP', '21399086': 'PWP', '19530750': 'PWP', '22810482': 'PWP', '22810485': 'PWP', '22810486': 'PWP', '27789658': 'PWP', '2100471738': 'PWP', '2100251354': 'PWP', '2101236398': 'PWP', '2101592556': 'PWP', '2101592554': 'PWP', '22810488': 'PWP', '19390976': 'PWP', '7477383': 'PWP', '7477384': 'PWP', '6531107': 'PWP', '9119112': 'PWP', '2100546245': 'PWP', '2100546246': 'PWP', '18280253': 'PWP', '22757945': 'PWP', '2100251355': 'PWP', '2100251356': 'PWP', '2101581477': 'PWP', '2101581485': 'PWP', '2101581486': 'PWP', '2101581487': 'PWP', '4187448': 'PWP', '4187449': 'PWP', '4182637': 'PWP', '5340337': 'PWP', '5268269': 'PWP', '5337565': 'PWP', '6235341': 'PWP', '4182871': 'PWP', '5344649': 'PWP', '5268266': 'PWP', '2101604811': 'PWP', '5268268': 'PWP', '2100543965': 'PWP', '7153866': 'PWP', '5351425': 'PWP', '21399085': 'PWP', '21331413': 'PWP', '24269563': 'PWP', '10903050': 'PWP', '10903051': 'PWP', '15594552': 'PWP', '15594555': 'PWP', '10903052': 'PWP', '20562158': 'PWP', '24229915': 'PWP', '2100123028': 'PWP', '10903112': 'PWP', '19146640': 'PWP', '2100564222': 'PWP', '24229916': 'PWP', '2100564223': 'PWP', '26256613': 'PWP', '38111491': 'PWP', '2100178024': 'PWP', '2100178025': 'PWP', '7296800': 'PWP', '7296801': 'PWP', '7296803': 'PWP', '6302739': 'PWP', '9119106': 'PWP', '7267178': 'PWP', '23510688': 'PWP', '2100124329': 'PWP', '23510689': 'PWP', '24381405': 'PWP', '2100124492': 'PWP', '3961028': 'PWP', '13432070': 'PWP', '13432072': 'PWP', '13432075': 'PWP', '13432077': 'PWP', '13432080': 'PWP', '13432083': 'PWP', '13432086': 'PWP', '13432088': 'PWP', '13432091': 'PWP', '5344779': 'PWP', '5337539': 'PWP', '5337474': 'PWP', '5338959': 'PWP', '5337542': 'PWP', '9119107': 'PWP', '3961029': 'PWP', '3961030': 'PWP', '5337465': 'PWP', '5337522': 'PWP', '5337533': 'PWP', '5337534': 'PWP', '2100542946': 'PWP', '5337537': 'PWP', '2100542947': 'PWP', '5337538': 'PWP', '5268270': 'PWP', '2100542948': 'PWP', '5337568': 'PWP', '2100124704': 'PWP', '5337551': 'PWP', '5337554': 'PWP', '5337557': 'PWP', '2100124705': 'PWP', '5337562': 'PWP', '5337468': 'PWP', '3961032': 'PWP', '5337569': 'PWP', '5337572': 'PWP', '5337575': 'PWP', '5096391': 'PWP', '5096393': 'PWP', '5337582': 'PWP', '5337585': 'PWP', '5268280': 'PWP', '5096396': 'PWP', '5344796': 'PWP', '5337576': 'PWP', '5337578': 'PWP', '9119108': 'PWP', '5344797': 'PWP', '5268272': 'PWP', '5268274': 'PWP', '9119109': 'PWP', '5096372': 'PWP', '5096373': 'PWP', '5096376': 'PWP', '5337588': 'PWP', '5337591': 'PWP', '5268279': 'PWP', '5337594': 'PWP', '24829133': 'PWP', '5337604': 'PWP', '5096381': 'PWP', '5337610': 'PWP', '5344798': 'PWP', '5337595': 'PWP', '5337597': 'PWP', '5337601': 'PWP', '9119110': 'PWP', '9119111': 'PWP', '9713927': 'PWP', '9713929': 'PWP', '9713930': 'PWP', '5344801': 'PWP', '5268275': 'PWP', '5268278': 'PWP', '5337608': 'PWP', '32613967': 'PWP', '2100543987': 'PWP', '5346844': 'PWP', '8961182': 'PWP', '8961183': 'PWP', '8961193': 'PWP', '11145858': 'PWP', '8961322': 'PWP', '11145859': 'PWP', '2100564221': 'PWP', '2101546336': 'PWP', '2101546338': 'PWP', '11145856': 'PWP', '9068313': 'PWP', '22757942': 'PWP', '27789659': 'PWP', '2101592555': 'PWP', '11145860': 'PWP', '9068312': 'PWP', '34104723': 'PWP', '2100088957': 'PWP'}
   #     return domain_map.get(str(product_id), None)

In [130]:
config=KaasAPIConfig()
a=config.getlookup()
b=config.get_domain_for_product('18576095')
a['5251493']


'HP Indigo 10000 Digital Press'

In [427]:

product_ids = ['2101057694', '236258', '90275', '90623', '90545', '90547', '90549', '3544544', '3544546', '2101097052', '5251493', '5251494', '2100719849', '2100537754', '2100126517', '2100126528', '5251495', '5251497', '2100126518', '2100126529', '34688149', '34688150', '34688151', '34688154', '35878165', '10799634', '10799635', '2100719850', '2100537735', '10799636', '10902891', '2100537734', '20945895', '20945896', '20945899', '34688174', '34688218', '34688219', '34688222', '35865637', '35865638', '35900353', '35865640', '3648450', '90556', '90558', '90548', '90560', '90559', '3648449', '90562', '90564', '90563', '5251498', '5251499', '2100126520', '2100126531', '2100126519', '2100126530', '5251500', '5251502', '37933302', '37933303', '34688163', '34688166', '90565', '3640220', '2100126557', '2100126572', '2100126556', '2100126571', '90568', '90570', '90569', '439129', '439130', '3382251', '3382252', '3382253', '2101097056', '90566', '90573', '3218087', '90575', '3223340', '3659874', '3244122', '2100126505', '90574', '5251504', '5251518', '2100126521', '2100126532', '5251533', '5251558', '4214301', '4214302', '2100126512', '2100126524', '4214310', '4214316', '37933299', '34688157', '34688158', '34702965', '35865641', '8954213', '8954214', '8954215', '8693693', '3648452', '3648451', '90705', '90707', '90706', '438409', '7826422', '7826423', '438413', '7826424', '7826426', '7826427', '7826429', '3252083', '3252084', '3252085', '2100126507', '2101097041', '3648459', '383572', '2100126558', '2100126573', '5338467', '5338468', '383574', '5350520', '383575', '3382246', '3382247', '3382249', '2101097028', '10902899', '10902900', '10902901', '10902904', '5226271', '5226272', '5226273', '5226275', '2100126513', '10799727', '10799728', '10799729', '10799732', '10902893', '10902894', '10902895', '10902898', '18021216', '18021217', '2100719846', '2100537703', '18021218', '18021221', '37933300', '37933301', '34766689', '34766692', '2101341287', '2101341290', '2101341301', '2101341317', '10902906', '10902907', '10902908', '10902910', '3722855', '3722856', '2100126514', '2100126525', '3722857', '3722859', '2101097032', '5350521', '4169552', '4169553', '4169661', '4169663', '5350522', '5226276', '5226277', '2100126515', '2100126526', '5226278', '5226280', '7186479', '7186480', '2100719847', '2100537675', '7186482', '7186484', '2100537674', '10799721', '10799722', '2100719848', '2100537696', '10799723', '10799726', '37933149', '37933150', '34702961', '34702964', '11503597', '11503704', '11503705', '11534765', '10799628', '10799629', '10799630', '10799633', '37910237', '37910238', '37921124', '37921126', '20540618', '20540619', '20540620', '20540624', '33990674', '33990675', '33990677', '33990680', '2101480396', '2101480397', '2101480398', '2101480399', '3919426', '3919427', '3919429', '3919431', '2100537651', '5251478', '5251479', '2100126516', '2100126527', '5251480', '5251482', '2100537669', '5173002', '5173003', '5173004', '5173006', '3827316', '3827317', '3827321', '3827324', '2100537647', '5172997', '5172998', '5172999', '5173001', '5251488', '5251489', '5251490', '5251492', '7186486', '7186487', '2100719845', '2100537679', '7186488', '7186490', '10799733', '10799734', '10799624', '10799627', '3648465', '90624', '31592', '31594', '90647', '90648', '90656', '90657', '212612', '212613', '212614', '212615', '90632', '90633', '3648466', '90680', '90694', '90695', '90682', '90683', '3648464', '90616', '91064', '90571', '2101057742', '2101057743', '2101057744', '2101571612', '2100469808', '2101576959', '2101587198', '8961173', '8961174', '8961175', '8961179', '26355293', '26355294', '21399086', '19530750', '22810482', '22810485', '22810486', '27789658', '2100471738', '2100251354', '2101236398', '2101592556', '2101592554', '22810488', '19390976', '7477383', '7477384', '6531107', '9119112', '2100546245', '2100546246', '18280253', '22757945', '2100251355', '2100251356', '2101581477', '2101581485', '2101581486', '2101581487', '4187448', '4187449', '4182637', '5340337', '5268269', '5337565', '6235341', '4182871', '5344649', '5268266', '2101604811', '5268268', '2100543965', '7153866', '5351425', '21399085', '21331413', '24269563', '10903050', '10903051', '15594552', '15594555', '10903052', '20562158', '24229915', '2100123028', '10903112', '19146640', '2100564222', '24229916', '2100564223', '26256613', '38111491', '2100178024', '2100178025', '7296800', '7296801', '7296803', '6302739', '9119106', '7267178', '23510688', '2100124329', '23510689', '24381405', '2100124492', '3961028', '13432070', '13432072', '13432075', '13432077', '13432080', '13432083', '13432086', '13432088', '13432091', '5344779', '5337539', '5337474', '5338959', '5337542', '9119107', '3961029', '3961030', '5337465', '5337522', '5337533', '5337534', '2100542946', '5337537', '2100542947', '5337538', '5268270', '2100542948', '5337568', '2100124704', '5337551', '5337554', '5337557', '2100124705', '5337562', '5337468', '3961032', '5337569', '5337572', '5337575', '5096391', '5096393', '5337582', '5337585', '5268280', '5096396', '5344796', '5337576', '5337578', '9119108', '5344797', '5268272', '5268274', '9119109', '5096372', '5096373', '5096376', '5337588', '5337591', '5268279', '5337594', '24829133', '5337604', '5096381', '5337610', '5344798', '5337595', '5337597', '5337601', '9119110', '9119111', '9713927', '9713929', '9713930', '5344801', '5268275', '5268278', '5337608', '32613967', '2100543987', '5346844', '8961182', '8961183', '8961193', '11145858', '8961322', '11145859', '2100564221', '2101546336', '2101546338', '11145856', '9068313', '22757942', '27789659', '2101592555', '11145860', '9068312', '34104723', '2100088957']
df_prod = pd.DataFrame(product_ids, columns=['product_id'])
df_prod.to_csv('kaas_products.csv', index=False)

In [3]:
def create_params():

    # Read the CSV file into a DataFrame
    df = pd.read_csv('kaas_products.csv')
    
    # Extract product IDs from the DataFrame
    product_ids = df['product_id'].astype(str).tolist()  # Convert IDs to strings
    
    # Disclosure levels (replace with actual levels or a method to get them)
    disclosure_levels = [
        "47406819852170807613486806879990",
        "696531864679532034919979251200881",
        "887243771386204747508092376253257",
        "287477763180518087286275037723076",
        "218620138892645155286800249901443",
        "600096605536507071488362545356335"
    ]

    batch_size = 4  # Number of product IDs in a batch
    
    # Generate batches and yield combinations
    for i in range(0, len(product_ids), batch_size):
        batch_product_ids = product_ids[i : i + batch_size]
        combined_product_ids = ",".join(batch_product_ids)
        for dl in disclosure_levels:
            yield combined_product_ids, dl
# list(create_params())

In [134]:
# def create_params1():
#     """
#     Generates product and disclosure level combinations for API requests based on configuration.
#     Yields:
#         tuple: A tuple containing (product ID, disclosure level).
#     """
#     product_params={'product':'2101057742, 2101057743, 2101057744, 2101571612, 2100469808, 2101576959, 2101587198, 8961173, 8961174, 8961175, 8961179, 26355293, 26355294, 21399086, 19530750, 22810482, 22810485, 22810486, 27789658, 2100471738, 2100251354, 2101236398, 2101592556, 2101592554, 22810488, 19390976, 7477383, 7477384, 6531107, 9119112, 2100546245, 2100546246, 18280253, 22757945, 2100251355, 2100251356, 2101581477, 2101581485, 2101581486, 2101581487, 4187448, 4187449, 4182637, 5340337, 5268269, 5337565, 6235341, 4182871, 5344649, 5268266, 2101604811, 5268268, 2100543965, 7153866, 5351425, 21399085, 21331413, 24269563, 10903050, 10903051, 15594552, 15594555, 10903052, 20562158, 24229915, 2100123028, 10903112, 19146640, 2100564222, 24229916, 2100564223, 26256613, 38111491, 2100178024, 2100178025, 7296800, 7296801, 7296803, 6302739, 9119106, 7267178, 23510688, 2100124329, 23510689, 24381405, 2100124492, 3961028, 13432070, 13432072, 13432075, 13432077, 13432080, 13432083, 13432086, 13432088, 13432091, 5344779, 5337539, 5337474, 5338959, 5337542, 9119107, 3961029, 3961030, 5337465, 5337522, 5337533, 5337534, 2100542946, 5337537, 2100542947, 5337538, 5268270, 2100542948, 5337568, 2100124704, 5337551, 5337554, 5337557, 2100124705, 5337562, 5337468, 3961032, 5337569, 5337572, 5337575, 5096391, 5096393, 5337582, 5337585, 5268280, 5096396, 5344796, 5337576, 5337578, 9119108, 5344797, 5268272, 5268274, 9119109, 5096372, 5096373, 5096376, 5337588, 5337591, 5268279, 5337594, 24829133, 5337604, 5096381, 5337610, 5344798, 5337595, 5337597, 5337601, 9119110, 9119111, 9713927, 9713929, 9713930, 5344801, 5268275, 5268278, 5337608, 32613967, 2100543987, 5346844, 8961182, 8961183, 8961193, 11145858, 8961322, 11145859, 2100564221, 2101546336, 2101546338, 11145856, 9068313, 22757942, 27789659, 2101592555, 11145860, 9068312, 34104723, 2100088957'}
#     params2 = {'disclosureLevel':'47406819852170807613486806879990,696531864679532034919979251200881,887243771386204747508092376253257,287477763180518087286275037723076,218620138892645155286800249901443,600096605536507071488362545356335'}
#     #pagination = {'resultStart':'0,300,600,900,1200,1500'}
#     product = [param.strip() for param in product_params['product'].split(',')]
#     disclosure_levels = params2['disclosureLevel'].split(',')
#     batch_size = 4  # Number of product IDs in a batch
#     for i in range(0, len(product), batch_size):
#         batch_product_ids = product[i:i + batch_size]
#         combined_product_ids = ','.join(batch_product_ids)
#         for dl in disclosure_levels:
#             yield combined_product_ids, dl
# #list(create_params())

In [4]:
import os
import datetime
import logging

def get_current_date():
    return datetime.datetime.now().strftime('%Y-%m-%d')


class LogConfig:
    """
    Configuration class for logging settings.
    """

    def __init__(self, log_dir="PROJECT_logs", log_level=logging.INFO, format_string="[%(asctime)s]^;%(levelname)s^;%(lineno)d^;%(filename)s^;%(funcName)s()^;%(message)s"):
        self.log_dir = log_dir
        self.log_level = log_level
        self.format_string = format_string

def get_log_file_name(prefix, date):
    """
    Generates a log file name with a given prefix and date.
    """
    return f"log_{prefix}_{date}.log"

def setup_logging(config=LogConfig()):
    """
    Sets up logging configuration based on provided LogConfig object.

    Args:
        config (LogConfig, optional): Configuration object with desired settings. Defaults to LogConfig().
    """
    os.makedirs(config.log_dir, exist_ok=True)

    # Determine current date
    current_date = get_current_date()

    # Set up all log file path
    all_log_file_path = os.path.join(config.log_dir, get_log_file_name(prefix="all", date=current_date))
    error_log_file_path = os.path.join(config.log_dir, get_log_file_name(prefix="error", date=current_date))

    # Set up all log handler
    all_handler = logging.FileHandler(all_log_file_path, mode="a")  # Append mode
    all_handler.setLevel(logging.DEBUG)
    all_handler.setFormatter(logging.Formatter(config.format_string))

    # Set up error log handler
    error_handler = logging.FileHandler(error_log_file_path, mode="a")  # Append mode
    error_handler.setLevel(logging.ERROR)
    error_handler.setFormatter(logging.Formatter(config.format_string))

    # Root logger configuration
    root_logger = logging.getLogger()
    root_logger.setLevel(logging.DEBUG)
    root_logger.addHandler(all_handler)
    root_logger.addHandler(error_handler)

def get_log_dataframe(file_path):
    data = []
    with open(file_path) as log_file:
        for line in log_file.readlines():
            data.append(line.split("^;"))

    log_df = pd.DataFrame(data)
    columns = ["Time stamp", "Log Level", "Line number", "File name", "Function name", "Message"]
    log_df.columns = columns
    
    log_df["log_message"] = log_df['Time stamp'].astype(str) + ": $" + log_df["Message"]

    return log_df[["log_message"]]




In [4]:
from opensearchpy import OpenSearch
import re
import json
import requests

In [5]:
def get_access_token():
    auth_url = 'https://css.api.hp.com/oauth/accesstoken'
    #'https://css.api.hp.com/knowledge/v2/generateEncryptedToken'
    auth_params = {
        'grant_type': 'client_credentials',
        'client_id': 'oVKELXf84JwfA1YKnAAAMt15mPs8T1BW',
        'client_secret':'FGU4NRkV9GmCNIWuL3P7LITu5Jt7Tgg5' #'byf9T3wXXcCljGKcPAWxs9sxow4EAA2J'
    }
    try:
        response = requests.post(auth_url, data=auth_params)
        response.raise_for_status()
        auth_data = response.json()
        access_token = response.json()["access_token"]
        if access_token:
            return access_token
        else:
            print("Error: Access token not found in response.")
            return None
    except requests.exceptions.RequestException as e:
        print(f"Error in authentication request: {e}")
        return None

access_token = get_access_token()
print( access_token)

eyJraWQiOiJhY2Nlc3NfdG9rZW4iLCJ0eXAiOiJKV1QiLCJhbGciOiJSUzI1NiJ9.eyJhdWQiOiJocGlvIiwibGVnYWxfem9uZSI6IkdMT0JBTCIsImVudmlyb25tZW50IjoicHJvZCIsImFwcGxpY2F0aW9uX25hbWUiOiJJbmR1c3RyaWFsUHJpbnRLbm93bGVkZ2VTZWFyY2gxNzA5MjIyMDkxOTc5IiwiYXBpX3Byb2R1Y3RfbGlzdCI6WyJDU1MtS05PV0xFREdFLUhQIEthYVMgQVBJIC0gUHJvZCJdLCJpc3MiOiJodHRwczpcL1wvY3NzLmFwaS5ocC5jb20iLCJzY29wZXMiOlsiIl0sImJ1X21ldGFfZGF0YSI6eyJrYWFzSWQiOiJJbmR1c3RyaWFsUHJpbnRLbm93bGVkZ2VTZWFyY2gifSwiZXhwIjoxNzI4Mjg2OTg1LCJpYXQiOjE3MjgyODMyODYsImNsaWVudF9pZCI6Im9WS0VMWGY4NEp3ZkExWUtuQUFBTXQxNW1QczhUMUJXIiwianRpIjoicnJ0LTBkNzAxNjBlM2NlMzQxMzBhLWQtZWEtMjc3MTMtNjY1OTQ3NjIyLTgifQ.MpYhwX-FPQBXtUch4FX3OJcRvNAYLm0Z8iyy238-gHXY-eo0Nh_WhpFRWOv3DF6_HWrfTRee6GYKk0T0j0AZj9hg2fWXiAqHSCLjHLVDmJcaT1JeT34o-5nKfuZ2OcUbAbw3m4ZEl6Q8GclXIE-oQ0sVLgS8HnauzTUMWtS9jXonmyB5qevT48mw8XmM-LpYN0vgB2eymoSCED4w2xF_qi8t3SHKTahsYorkTM1Giggbj5rCw_koBNL5UTXnosZ_4R-PaFUvkgQdi37cWx7DZ_B6B13FKyeR3Wfdwsu7r_NSAo37r5h1jbGQPXVJyAydohYbaBHb19bgJql2xk13Eg


In [22]:
# email code
import pandas as pd
import smtplib
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText
from email.mime.application import MIMEApplication
import io

def send_error_report_email(email_df, sender_email, receiver_email):
    email_df['documentID'] = email_df['Record'].apply(lambda x: x['documentID'])
    email_df['Domain'] = email_df['Record'].apply(lambda x: x['Domain'])
    email_df['contentUpdateDate'] = email_df['Record'].apply(lambda x: x['contentUpdateDate'])
    email_df['error_message'] = email_df['Error'].apply(lambda x: x.split(', ')[2])
    email_df.drop(columns=['Record','Error'],inplace=True)

    # Save DataFrame to an Excel file
    csv_filename = 'error_data.xlsx'

    # Create a multipart message
    message = MIMEMultipart()
    message["From"] = sender_email
    message["To"] = receiver_email
    message["Subject"] = "Error Report"

    # Add body text
    body = """Dear [Recipient],\n\nI hope this message finds you well.\nPlease find the attached file containing the report for the KAAS data ingest errors.\n\nIf you have any questions or need further clarification, feel free to reach out.\n\nBest regards,\n---"""
    message.attach(MIMEText(body, "plain"))

    # Convert DataFrame to Excel in memory
    in_memory_fp = io.BytesIO()
    email_df.to_excel(in_memory_fp, index=False)
    
    # Add the Excel file as an attachment
    part = MIMEApplication(in_memory_fp.getvalue(), Name=csv_filename)
    # After the file is closed
    part['Content-Disposition'] = 'attachment; filename="%s"' % csv_filename
    message.attach(part)
    smtp=config.smtp
    # Connect to the SMTP server and send email
    with smtplib.SMTP(smtp) as smtp:
        smtp.sendmail(sender_email, receiver_email, message.as_string())



# Example usage
config = SMTPEmailConfig()
sender_email = config.sender_email
receiver_email = config.receiver_email

send_error_report_email(email_df, sender_email, receiver_email)


In [7]:
def fetch_opensearch_data(client,documentID,index_name ):
    query = {
        "query": {
            "match": {
                "documentID": documentID
            }
        }
    }
    result = client.search(index=index_name, body=query)
    item_list = [hit for hit in result['hits']['hits']]
    return item_list


In [ ]:
    def make_api_request(self):
        # Get configuration
        config = KaasAPIConfig()
        access_token = get_access_token()

        # Define base parameters for API request
        base_params = {
            "resultLimit": "3000",
            #'fromDate': KaasAPI.fromDate,
            "printFields": "documentID,title,contenttypeheader,product,contenttype,contentupdatedate,languagecode,disclosurelevel,store,description,renderlink,ishType,technicalLevel,productstagged,hpid",
        }

        df = pd.DataFrame()
        params_generator = create_params()

        for v1, v2 in params_generator:
            params = base_params.copy()
            params["product"] = v1
            params["disclosureLevel"] = v2
            url = config.api_base_url
            headers = {
                "Content-Type": "application/json",
                "Authorization": "Bearer " + access_token,
            }

            try:
                # Make API request
                response = requests.get(url, params=params, headers=headers)
                response.raise_for_status()
            except requests.exceptions.HTTPError as e:
                raise e
            try:
                # Parse response JSON
                data = response.json()
            except ValueError as e:
                # Log error and raise exception if response is not valid JSON
                logging.error("Error: Response is not valid JSON.")
                raise e

            if response.status_code == 200:
                # Process successful response
                matches_data = data.get("matches", [])
                df1 = pd.DataFrame(matches_data)
                df = pd.concat([df, df1])
                df = df.drop_duplicates(subset="documentID", keep="last")
            else:
                # Log error and raise exception if response status code is not 200
                logging.error(f"Error: {response.status_code}")
                raise Exception(f"Error: {response.status_code}")

        logging.info(f"Retrieved data after handling duplicates: {df.shape[0]} records")
        return df

In [6]:
import pandas as pd
import numpy as np
import datetime
from concurrent.futures import ThreadPoolExecutor, as_completed
class KaasAPI():
    fromDate = '2024-08-13'
    failed_records_df = pd.DataFrame(columns=["Record", "Error", "Source"])
    def make_api_request(self):
        # Get configuration
        config = KaasAPIConfig()
        access_token = get_access_token()
        
        # Define base parameters for API request
        base_params = {
            "resultLimit": "3000",
            # 'fromDate': KaasAPI.fromDate,
            "printFields": "documentID,title,contenttypeheader,product,contenttype,contentupdatedate,languagecode,disclosurelevel,store,description,renderlink,ishType,technicalLevel,productstagged,hpid",
        }
        
        df = pd.DataFrame()
        params_generator = create_params()
        
        def fetch_data(v1, v2):
            # Function to make a single API request
            params = base_params.copy()
            params["product"] = v1
            params["disclosureLevel"] = v2
            url = config.api_base_url
            headers = {
                "Content-Type": "application/json",
                "Authorization": "Bearer " + access_token,
            }
            response = requests.get(url, params=params, headers=headers)
            response.raise_for_status()
            data = response.json()
            return pd.DataFrame(data.get("matches", []))
        
        # Use ThreadPoolExecutor to run requests in parallel
        with ThreadPoolExecutor(max_workers=10) as executor:
            futures = [executor.submit(fetch_data, v1, v2) for v1, v2 in params_generator]
            for future in as_completed(futures):
                df1 = future.result()
                df = pd.concat([df, df1])
        
        df = df.drop_duplicates(subset="documentID", keep="last")
        return df
    def preprocess_data(self, df):
        try:
            # Get lookup data from configuration
            config = KaasAPIConfig()
            lookup = config.getlookup()
            parent_doc_mapping = pd.read_csv("parentDoc_mapping.csv")

            # Merge main DataFrame with parentDoc mapping
            df = pd.merge(
                df,
                parent_doc_mapping,
                how="left",
                left_on="documentID",
                right_on="documentID",
            )
            df['description']=df['description'].apply(lambda x: re.sub(r'(<img.*?>|<iframe.*?>|<.*?>|\xa0)', '', x).replace('\n', ' ').strip())
            # Combine title and description columns
            df["ti_desc_prod"] = df['title'].fillna('') + ' ' + df['description'].fillna('') + ' ' + df['documentID'].fillna('')

            df["ti_desc_prod"] = df["ti_desc_prod"].replace(r"^\s*$", "N/A", regex=True)
            df['ti_desc_prod']=df['ti_desc_prod'].apply(lambda x: re.sub(r'<.*?>', '', x))
            
            # Create Doc_status field
            df["Doc_Status"] = df["ti_desc_prod"].apply(
                lambda x: "rejected" if x == "N/A" else "published"
            )
            df['Domain'] = df['products'].apply(
            lambda products: set(filter(None, (config.get_domain_for_product(product_id) for product_id in products))) if products else None)
            df['Domain'] = df['Domain'].apply(lambda x: ', '.join(x) if isinstance(x, set) else '')
            
            mask = df['Domain'] == ''
            # Apply the domain extraction logic only to the filtered rows
            df.loc[mask, 'Domain'] = np.where(df.loc[mask, 'ti_desc_prod'].str.contains('Indigo', case=False), 'Indigo',
                                               np.where(df.loc[mask, 'ti_desc_prod'].str.contains('PageWide', case=False), 'PWP', ''))

            # Map product IDs to product names
            df["product_info"] = df.apply(
                lambda row: [
                    lookup[str(id)] for id in row["products"] if str(id) in lookup
                ],
                axis=1,
            )
            language_code_mapping = {
                'English': 'en',
                'EN': 'en',
                'En': 'en',
                'Chinese': 'zh',
                'French': 'fr',
                'German': 'de',
                'Japanese': 'ja',
                'Korean': 'ko',
                'Portuguese': 'pt',
                'Russian': 'ru',
                'Spanish': 'es',
                'Italian': 'it',
                'Simplified_Chinese': 'zh-CN',
                'Portuguese-Br': 'pt-BR',
                'Hebrew': 'he',
                'Spanish_Latam': 'es-419',
                'Hungarian': 'hu',
                'Dutch': 'nl',
                'Other Languages': 'xx'  # Handling other unspecified languages
            }
            
            # Strip whitespace and normalize case
            df['language'] = df['language'].str.strip().str.title()
            
            # Replace the language names with their corresponding ISO codes
            df['language'] = df['language'].replace(language_code_mapping)
            # Map disclosureLevel to persona
            persona_map = {
                "287477763180518087286275037723076": "Operator",
                "47406819852170807613486806879990": "Engineer",
                "696531864679532034919979251200881": "Operator",
                "600096605536507071488362545356335":"Engineer",
                "218620138892645155286800249901443":"Operator",
                "887243771386204747508092376253257":"Engineer"
            }

            df["persona"] = df["disclosureLevel"].replace(persona_map)
            
            df['renderLink'] = df['renderLink'].apply(lambda x: x if isinstance(x, str) and len(x) < 100 else None)

            # Drop unnecessary columns
            df.drop(columns=["products", "topIssue"], inplace=True)

            # Rename column
            df.rename(
                columns={"Pdfs": "parentDoc", "product_info": "products"}, inplace=True
            )
            
            df["parentDoc"] = df["parentDoc"].replace("N/A", "")
            df.fillna("", inplace=True)

            df["parentDoc"] = df["parentDoc"].replace(r"^\s*$", None, regex=True)
            df['renderLink'] = df['renderLink'].replace(r"^\s*$", None, regex=True)

            df['products'] = df['products'].apply(lambda x: list(set(x)) if x not in [None, ''] else [])

            return df
        except Exception as e:
            logging.error("An error occurred during preprocessing: %s", str(e))
            raise

    def index_data_to_opensearch_test(self, df, index_name):
        # Connect to OpenSearch
        config1 = OpenSearchConnectConfigStg()
        timeout_seconds = 160
        client = OpenSearch(
            hosts=[{'host': config1.host, 'port': config1.port}],
            http_compress=True,
            http_auth=config1.auth,
            use_ssl=config1.use_ssl,
            verify_certs=config1.verify_certs,
            timeout=timeout_seconds
        )
    
        dict_list = df.to_dict(orient="records")
        document_ids = [record["documentID"] for record in dict_list]
        
        # Batch fetch existing documents
        existing_docs = fetch_existing_documents(client, index_name, document_ids)
    
        # Initialize counters and lists
        successful_records = 0
        failed_records = []
        new_records = 0
        updated_records = 0
    
        # Prepare actions for bulk indexing with upsert
        actions = []
        for record in dict_list:
            if existing_docs.get(record["documentID"], False):
                updated_records += 1
            else:
                new_records += 1
    
            action = {
                "_index": index_name,
                "_id": record["documentID"],
                "pipeline": "doccebo.v2.emb_pipeline",
                "_op_type": "update",
                "doc": record,
                "doc_as_upsert": True,
            }
            actions.append(action)
    
        # Perform bulk indexing with upsert
        try:
            success, _ = bulk(client, actions=actions)
            successful_records = success
        except Exception as e:
            # Log and store failed records
            for record in dict_list:
                failed_records.append((record, str(e), "KAAS_API"))
                logging.error(
                    f"Failed to index document {record}: {e}  : 'KAAS_API_INGRESS'"
                )
    
        # Store failed records and update fromDate if necessary
        if failed_records:
            logging.info(
                f"Indexing completed with {len(failed_records)} failed records."
            )
            self.store_failed_records(failed_records)
        else:
            # Update fromDate attribute if all records are successful
            current_datetime = datetime.datetime.now()
            KaasAPI.fromDate = current_datetime.strftime("%Y-%m-%d")
            logging.info("All records indexed successfully. Updating fromDate.")
    
        # Log indexing statistics to 'kas_log_index' index
        try:
            data_to_index = {
                "successful_records": successful_records,
                "failed_records": len(failed_records),
                "new_records": new_records,
                "updated_records": updated_records,
                "timestamp": datetime.datetime.now(),
                "Source": 'KAAS_API_DATA_INGESTION',
                "index_loaded": index_name,
            }
            client.index(index="kas_log_index", body=data_to_index)
            logging.info("Successfully indexed data to kas_log_index.")
        except Exception as e:
            logging.error(f"Failed to index data to kas_log_index: {e}")
        logging.info(
            "successful_records: %s ::: failed_records: %s",
            successful_records,
            failed_records,
        )
    
        return successful_records, len(failed_records)

    def store_failed_records(self, failed_records):
        try:
            # Check if the DataFrame is empty
            if len(KaasAPI.failed_records_df) == 0:
                # Initialize failed_records_df if it's empty
                KaasAPI.failed_records_df = pd.DataFrame(
                    columns=["Record", "Error", "Source"]
                )

            # Convert failed_records to DataFrame
            failed_records_df_new = pd.DataFrame(
                failed_records, columns=["Record", "Error", "Source"]
            )

            # Concatenate new records with existing DataFrame
            KaasAPI.failed_records_df = pd.concat(
                [KaasAPI.failed_records_df, failed_records_df_new], ignore_index=True
            )

            # Log success message
            logging.info(
                f"Failed records stored successfully. Total failed records: {len(KaasAPI.failed_records_df)}"
            )

            # Return updated DataFrame
            return KaasAPI.failed_records_df
        except Exception as e:
            # Log error if storing failed records fails
            logging.error(f"Failed to store failed records: {e}")
            return None

    def kaas_job(self):
        try:
            df = self.make_api_request()
            df = self.preprocess_data(df)
            result = self.index_data_to_opensearch(df, index_name="kaas.v5.dev")
            return result
        except Exception as e:
            logging.error("An error occurred during kaas_job: %s", str(e))
            raise


In [19]:
import requests
import pandas as pd
from concurrent.futures import ThreadPoolExecutor, as_completed

def make_api_request1(self):
    # Get configuration
    config = KaasAPIConfig()
    access_token = get_access_token()

    # Define base parameters for API request
    base_params = {
        "resultLimit": "3000",
        #'fromDate': KaasAPI.fromDate,
        "printFields": "documentID,title,contenttypeheader,product,contenttype,contentupdatedate,languagecode,disclosurelevel,store,description,renderlink,ishType,technicalLevel,productstagged,hpid",
    }

    df = pd.DataFrame()
    params_generator = create_params()

    def fetch_data(v1, v2):
        # Function to make a single API request
        params = base_params.copy()
        params["product"] = v1
        params["disclosureLevel"] = v2
        url = config.api_base_url
        headers = {
            "Content-Type": "application/json",
            "Authorization": "Bearer " + access_token,
        }
        response = requests.get(url, params=params, headers=headers)
        response.raise_for_status()
        data = response.json()
        return pd.DataFrame(data.get("matches", []))

    # Use ThreadPoolExecutor to run requests in parallel
    with ThreadPoolExecutor(max_workers=10) as executor:
        futures = [executor.submit(fetch_data, v1, v2) for v1, v2 in params_generator]
        for future in as_completed(futures):
            df1 = future.result()
            df = pd.concat([df, df1])

    df = df.drop_duplicates(subset="documentID", keep="last")
    return df
import time
start=time.time()
check=make_api_request()
end=time.time()
print(end-start)

NameError: name 'make_api_request' is not defined

In [7]:
def fetch_existing_documents(client, index_name, document_ids):
    try:
        response = client.mget(index=index_name, body={"ids": document_ids})
        return {doc["_id"]: doc["found"] for doc in response["docs"]}
    except Exception as e:
        logging.error(f"Failed to fetch existing documents: {e}")
        return {}


In [24]:
import pandas as pd
import logging
# setup_logging()
result=KaasAPI()

In [25]:
df=result.make_api_request()

In [26]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5638 entries, 0 to 4
Data columns (total 18 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   documentID         5638 non-null   object 
 1   title              5638 non-null   object 
 2   contentTypeHeader  5638 non-null   object 
 3   renderLink         5638 non-null   object 
 4   matchScore         5638 non-null   float64
 5   description        5638 non-null   object 
 6   contentUpdateDate  5638 non-null   object 
 7   language           5638 non-null   object 
 8   disclosureLevel    5638 non-null   object 
 9   contentType        5638 non-null   object 
 10  store              5638 non-null   object 
 11  docSource          5638 non-null   object 
 12  topIssue           0 non-null      object 
 13  products           5638 non-null   object 
 14  ishType            5638 non-null   object 
 15  hpID               5638 non-null   object 
 16  technicalLevel     5638 non-null

In [98]:
# CSETOOL-7413 INC8825320 
df1[~df1['documentID'].str.startswith(('ish','pdf','c0','REF'))]


documentID  \
5612  5e337a6e2ad5684e24fd8fdf5d4492254748908d   

                                        title contentTypeHeader renderLink  \
5612  How to Find Your Printer Name or Number                         None   

      matchScore                                        description  \
5612    7.000131  Learn how to check your printer and its labels...   

        contentUpdateDate language                    disclosureLevel  \
5612  2024-06-24 22:00:07       en  696531864679532034919979251200881   

     contentType  ... ishType hpID technicalLevel position parentDoc  \
5612              ...      NA  N/A                      13      None   

                                           ti_desc_prod Doc_Status Domain  \
5612  How to Find Your Printer Name or Number Learn ...  published          

     products   persona  
5612       []  Operator  

[1 rows x 22 columns]

In [15]:
df1[df1['documentID']=='pdf_3999714_en-US-6']

documentID title contentTypeHeader renderLink  matchScore  \
1364  pdf_3999714_en-US-6         Product Support       None         7.0   

     description    contentUpdateDate language  \
1364              2021-07-28 05:57:47       en   

                       disclosureLevel       contentType  ... ishType hpID  \
1364  47406819852170807613486806879990  Use and Maintain  ...      NA  N/A   

     technicalLevel position parentDoc           ti_desc_prod Doc_Status  \
1364                     602      None    pdf_3999714_en-US-6  published   

      Domain                                           products   persona  
1364  Indigo  [HP Indigo s2000 Digital Press, HP Indigo 2000...  Engineer  

[1 rows x 22 columns]

In [27]:
df1=result.preprocess_data(df)

In [28]:
df1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5650 entries, 0 to 5649
Data columns (total 22 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   documentID         5650 non-null   object 
 1   title              5650 non-null   object 
 2   contentTypeHeader  5650 non-null   object 
 3   renderLink         59 non-null     object 
 4   matchScore         5650 non-null   float64
 5   description        5650 non-null   object 
 6   contentUpdateDate  5650 non-null   object 
 7   language           5650 non-null   object 
 8   disclosureLevel    5650 non-null   object 
 9   contentType        5650 non-null   object 
 10  store              5650 non-null   object 
 11  docSource          5650 non-null   object 
 12  ishType            5650 non-null   object 
 13  hpID               5650 non-null   object 
 14  technicalLevel     5650 non-null   object 
 15  position           5650 non-null   int64  
 16  parentDoc          3198 

In [29]:
result.index_data_to_opensearch_test(df1,'kaas.v5.dev')

C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\opensearchpy\connection\http_urllib3.py:208: UserWarning: Connecting to https://vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com:443 using SSL with verify_certs=False is insecure.
  warnings.warn(
C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urlli

(5650, 0)

In [35]:
from opensearchpy import OpenSearch, helpers

def index_data_to_opensearch(index_name, df):
    # Connect to OpenSearch
    config1 = OpenSearchConnectConfigDev()
    timeout_seconds = 160
    client = OpenSearch(
        hosts=[{'host': config1.host, 'port': config1.port}],
        http_compress=True,
        http_auth=config1.auth,
        use_ssl=config1.use_ssl,
        verify_certs=config1.verify_certs,
        timeout=timeout_seconds
    )

    # Retrieve data, preprocess, and convert to dictionary
    dict_list = df.to_dict(orient='records')

    # Initialize counters and lists
    successful_records = 0
    failed_records = []

    # Prepare actions for bulk indexing with upsert
    actions = [
        {
            "_index": index_name,
            "_id": record["documentID"],
            "_op_type": "update",
            "pipeline": "doccebo.v2.emb_pipeline",  # Add the pipeline to be triggered
            "doc": record,
            "doc_as_upsert": True  # Upsert if document doesn't exist
        }
        for record in dict_list
    ]

    # Perform bulk indexing
    try:
        success, _ = helpers.bulk(client, actions=actions)
        successful_records = success
    except Exception as e:
        # Log and store failed records
        for record in dict_list:
            failed_records.append((record, str(e), 'KAAS_API'))
            #logging.error(f"Failed to index document {record['_id']}: {e}")

    return successful_records, len(failed_records)

# Setup logging
# setup_logging()
#index_data_to_opensearch('kaas.v5.dev', df1)


In [61]:
    def make_api_request(document_ID):
        # Get configuration
        config = KaasAPIConfig()
        access_token = get_access_token()
        # Define base parameters for API request
        base_params = {
            'resultLimit': '100',
            #'fromDate': self.fromDate,  # Use self.fromDate to access class attribute
            'printFields': 'documentID,title,contenttypeheader,product,contenttype,contentupdatedate,languagecode,disclosurelevel,store,description,renderlink,ishType,technicalLevel,productstagged,hpid'
        }

        df = pd.DataFrame()
        batch_size = 5
        for i in document_ID:
            base_params['documentID'] = i
            url = config.api_base_url
            #config.api_base_url
            headers = {
                'Content-Type': 'application/json',
                #'accessToken': '00026d3wMvYtIw9AqUSR2N4Nc0Zq'
                "Authorization": "Bearer " + access_token
            }
            try:
                # Make API request
                response = requests.get(url, params=base_params, headers=headers)
                response.raise_for_status()
            except requests.exceptions.RequestException as e:
                # Log error if request fails
                logging.error(f"Error in API request: {e}")
                print(e)
                return None

            try:
                # Parse response JSON
                data = response.json()
            except ValueError:
                # Log error if response is not valid JSON
                logging.error("Error: Response is not valid JSON.")
                return None

            if response.status_code == 200:
                # Process successful response
                matches_data = data.get('matches', [])
                df1 = pd.DataFrame(matches_data)
                df = pd.concat([df, df1])
                # Keep only the latest updated records
                df = df.drop_duplicates(subset='documentID', keep='last')
            else:
                # Log error if response status code is not 200
                print(f"Error: {response.status_code}")
                logging.error(f"Error: {response.status_code}")
                return None

        logging.info(f"Retrieved data after handling duplicates: {df.shape[0]} records")
        return df

In [74]:
from opensearchpy import OpenSearch
from opensearchpy.helpers import bulk

def index_data_to_opensearch(index_name,df):
    # Connect to OpenSearch
    config1 = OpenSearchConnectConfig()
    timeout_seconds = 160
    client = OpenSearch(
        hosts=[{'host': config1.host, 'port': config1.port}],
        http_compress=True,
        http_auth=config1.auth,
        use_ssl=config1.use_ssl,
        verify_certs=config1.verify_certs,
        timeout=timeout_seconds
    )

    # Retrieve data, preprocess, and convert to dictionary

    dict_list = df.to_dict(orient='records')

    # Initialize counters and lists
    successful_records = 0
    failed_records = []

    # Prepare actions for bulk indexing
    actions = [
        {
            "_index": index_name,
            "_id": record["documentID"],
            "_source": record
        }
        for record in dict_list
    ]

    # Perform bulk indexing
    try:
        success, _ = bulk(client, actions=actions)
        successful_records = success
    except Exception as e:
        # Log and store failed records
        for record in dict_list:
            failed_records.append((record, str(e), 'KAAS_API'))
            #logging.error(f"Failed to index document {record['_id']}: {e}")

    return successful_records, len(failed_records)
#setup_logging()
index_data_to_opensearch('data_quality_check_iteration',test_df)

C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\opensearchpy\connection\http_urllib3.py:208: UserWarning: Connecting to https://vpc-kcs-isearch-wao6ffx5mlzga2q2heyie7jigu.us-west-2.es.amazonaws.com:443 using SSL with verify_certs=False is insecure.
  warnings.warn(
C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-kcs-isearch-wao6ffx5mlzga2q2heyie7jigu.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
--- Logging error ---
Traceback (most recent call last):
  File "C:\Users\KuBP064\AppData\Local\anaconda3\Lib\logging\__init__.py", line 1113, in emit
    stream.write(msg + self.terminator)
  File "C:\Users\KuBP064\AppData\Local\anaconda3\Lib\encodings\cp1252.py", line 19, in encode
    return codecs.charmap_encode(input,self.errors,enc

(5571, 0)

In [16]:
# DataQualityProcessor
import pandas as pd

class DataQualityProcessor:

    @staticmethod
    def get_value(row, column):
        """ Helper method to safely get a value from a row, returning an empty string if the column is missing. """
        return row[column] if column in row else ''

    @staticmethod
    def generate_remarks(row, include_id=False, include_catalog_number=False):
        remarks = {
            'documentID': DataQualityProcessor.get_value(row, 'documentID'),
            'title': DataQualityProcessor.get_value(row, 'title'),
            'products': DataQualityProcessor.get_value(row, 'products'),
            'persona': DataQualityProcessor.get_value(row, 'persona'),
            'description': DataQualityProcessor.get_value(row, 'description'),
            'contentUpdateDate': DataQualityProcessor.get_value(row, 'contentUpdateDate'),
            'Domain': DataQualityProcessor.get_value(row, 'Domain'),
            'Doc_Status': DataQualityProcessor.get_value(row, 'Doc_Status'),
            'language': DataQualityProcessor.get_value(row, 'language'),
            'Title_is_too_short': 'N',
            'Description_is_too_short': 'N',
            'Domain_is_empty': 'N',
            'Title_is_empty': 'N',
            'Description_is_empty': 'N',
            'Disclosure_Level_is_empty': 'N',
            'Persona_is_empty': 'N',
            'Products_is_empty': 'N',
            'catalog_number_is_empty': 'N'
        }

        # Assign 'id' based on include_id flag
        remarks['id'] = DataQualityProcessor.get_value(row, 'id') if include_id else None
    
        # Assign 'catalog_number' based on include_catalog_number flag
        remarks['catalog_number'] = DataQualityProcessor.get_value(row, 'catalog_number') if include_catalog_number else None
   
        # Check if catalog_number is empty
        if 'catalog_number' in row and row['catalog_number'] == '':
            remarks['catalog_number_is_empty'] = 'Y'
    
        if len(remarks['title']) < 15 and len(remarks['title']) > 0:
            remarks['Title_is_too_short'] = 'Y'
    
        if len(remarks['description']) < 30 and len(remarks['description']) > 0:
            remarks['Description_is_too_short'] = 'Y'
    
        if remarks['Domain'] == '':
            remarks['Domain_is_empty'] = 'Y'
    
        if remarks['title'] == '':
            remarks['Title_is_empty'] = 'Y'
    
        if remarks['description'] == '':
            remarks['Description_is_empty'] = 'Y'
    
        if 'disclosureLevel' in row and row['disclosureLevel'] == '':
            remarks['Disclosure_Level_is_empty'] = 'Y'
    
        if 'persona' in row and row['persona'] == '':
            remarks['Persona_is_empty'] = 'Y'
    
        if 'products' in row and (row['products'] is None or len(row['products']) == 0):
            remarks['Products_is_empty'] = 'Y'
    
        return remarks


    @staticmethod   
    def process_dataframe(df,index_name,include_id, include_catalog_number):
        
        remarks_info = df.apply(DataQualityProcessor.generate_remarks, axis=1, include_id=include_id, include_catalog_number=include_catalog_number)
        df_remarks = pd.DataFrame(remarks_info.tolist())
        df_remarks["Index_Name"] =index_name
        df_remarks["Source"]= index_name.split('.')[0]
        df_remarks['contentUpdateDate'] = pd.to_datetime(df_remarks['contentUpdateDate']).dt.strftime('%Y-%m-%d %H:%M:%S')
        df_remarks.fillna('',inplace=True)
        df_remarks['Contents'] = df_remarks.apply(lambda row: {
            'title': row['title'],
            'products': row['products'],
            'persona': row['persona'],
            'description': row['description'],
            'contentUpdateDate': row['contentUpdateDate'],
            'Domain': row['Domain']
        }, axis=1)
        df_remarks['Contents']=df_remarks['Contents'].apply(lambda x:str(x))
        df_remarks=df_remarks.drop(columns=['products', 'persona'])
        columns_to_check = [
            "Title_is_too_short",
            "Description_is_too_short",
            "Domain_is_empty",
            "Title_is_empty",
            "Description_is_empty",
            "Disclosure_Level_is_empty",
            "Persona_is_empty",
            "Products_is_empty"
        ]
        if index_name.split('.')[0] =='kz':
            columns_to_check.append('catalog_number_is_empty')

        # Create the 'issues' column
        df_remarks['contains_issue'] = df_remarks[columns_to_check].apply(lambda row: 'Y' if 'Y' in row.values else 'N', axis=1)
        
        if 'kaas' in index_name:
            mask = df_remarks['documentID'].str.contains('ish') & (df_remarks['Title_is_too_short'] == 'Y')
            # Update the 'Title_is_too_short' column to 'N' for the filtered records
            df_remarks.loc[mask, 'Title_is_too_short'] = 'N'
            
        return df_remarks

    @staticmethod
    def generate_qc_data_log(test_df,index_name):
        index_name = index_name
        columns_to_check = [
            "Title_is_too_short",
            "Description_is_too_short",
            "Domain_is_empty",
            "Title_is_empty",
            "Description_is_empty",
            "Disclosure_Level_is_empty",
            "Persona_is_empty",
            "Products_is_empty",
            "contains_issue"
        ]
        
        # Append 'catalog_number_is_empty' if index_name starts with 'kz'
        if index_name.startswith('kz'):
            columns_to_check.append('catalog_number_is_empty')
        
        # Create dictionary to store counts using lambda
        count_dict = {
        col: test_df[col].value_counts().get('Y', 0) 
        for col in columns_to_check 
        if col in test_df.columns
        } 
        
        date_time = datetime.datetime.now()
        count_dict['datetime'] = date_time.strftime('%Y-%m-%d %H:%M:%S')
        count_dict['date'] = date_time.strftime('%Y-%m-%d')
        count_dict['source'] = index_name.split('.')[0]
        
        return count_dict

    @staticmethod
    def index_data_to_opensearch(df,index_name,qc_data_log):
        # Connect to OpenSearch
        config1 = OpenSearchConnectConfigStg()
        timeout_seconds = 160
        client = OpenSearch(
            hosts=[{'host': config1.host, 'port': config1.port}],
            http_compress=True,
            http_auth=config1.auth,
            use_ssl=config1.use_ssl,
            verify_certs=config1.verify_certs,
            timeout=timeout_seconds
        )
    
        # Retrieve data, preprocess, and convert to dictionary
    
        dict_list = df.to_dict(orient='records')
        print(dict_list)
        # Initialize counters and lists
        successful_records = 0
        failed_records = []
    
        # Prepare actions for bulk indexing
        actions = [
            {
                "_index": index_name,
                "_id": record["documentID"],
                "_op_type": "update",
                "doc": record,
                "doc_as_upsert": True  # Upsert if document doesn't exist
            }
            for record in dict_list
        ]

        try:
            success, _ = bulk(client, actions=actions)
            successful_records = success
        except Exception as e:
            # Log and store failed records
            for record in dict_list:
                failed_records.append((record, str(e), index_name.split('.')[0]))
                # logging.error(f"Failed to index document {record['_id']}: {e}")
        try:
            client.index(index='data_quality_check_datalog', body=qc_data_log)
        except Exception as e:
            raise
        return successful_records, len(failed_records)

In [30]:
test_df=DataQualityProcessor.process_dataframe(df1,'kaas.v5.dev',False,False)

In [31]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5650 entries, 0 to 5649
Data columns (total 22 columns):
 #   Column                     Non-Null Count  Dtype 
---  ------                     --------------  ----- 
 0   documentID                 5650 non-null   object
 1   title                      5650 non-null   object
 2   description                5650 non-null   object
 3   contentUpdateDate          5650 non-null   object
 4   Domain                     5650 non-null   object
 5   Doc_Status                 5650 non-null   object
 6   language                   5650 non-null   object
 7   Title_is_too_short         5650 non-null   object
 8   Description_is_too_short   5650 non-null   object
 9   Domain_is_empty            5650 non-null   object
 10  Title_is_empty             5650 non-null   object
 11  Description_is_empty       5650 non-null   object
 12  Disclosure_Level_is_empty  5650 non-null   object
 13  Persona_is_empty           5650 non-null   object
 14  Products

In [32]:
qc_data_log=DataQualityProcessor.generate_qc_data_log(test_df,'kaas.v5.dev')
qc_data_log

{'Title_is_too_short': 19,
 'Description_is_too_short': 356,
 'Domain_is_empty': 20,
 'Title_is_empty': 1,
 'Description_is_empty': 570,
 'Disclosure_Level_is_empty': 0,
 'Persona_is_empty': 0,
 'Products_is_empty': 40,
 'contains_issue': 1409,
 'datetime': '2024-10-08 08:46:45',
 'date': '2024-10-08',
 'source': 'kaas'}

In [33]:
DataQualityProcessor.index_data_to_opensearch(test_df,'data_quality_check_iteration',qc_data_log)

C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\opensearchpy\connection\http_urllib3.py:208: UserWarning: Connecting to https://vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com:443 using SSL with verify_certs=False is insecure.
  warnings.warn(
IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.wa

(5650, 0)

In [174]:
# ## PRODUCTS MAPPING FROM TAXONOMY-KAAS-LEVEL-3
# ipmap=pd.read_excel(r"C:\Users\KuBP064\Downloads\HP KM POC - taxonomy fields - 2.0 - Copy (1).xlsx",sheet_name='Indigo')
# ppmap=pd.read_excel(r"C:\Users\KuBP064\Downloads\HP KM POC - taxonomy fields - 2.0 - Copy (1).xlsx",sheet_name='PWP')
# ipmap=ipmap[['level2','level3','level5','Unnamed: 6']].iloc[3:].reset_index(drop=True)
# ppmap=ppmap[['level2','level3','level5','4211033']].iloc[3:]
# ipmap['p_name']=ipmap['level3'].fillna(method='ffill')
# ppmap['p_name']=ppmap['level3'].fillna(method='ffill')
# ipmap['domain']='Indigo'
# ppmap['domain']='PWP'
# indigo = {f'{i}': j for i, j in zip(ipmap['Unnamed: 6'], ipmap['p_name'])}
# indigo.update({f'{i}': j for i, j in zip(ppmap['4211033'], ppmap['p_name'])})
# product_d = {f'{i}': j for i, j in zip(ipmap['Unnamed: 6'],ipmap['domain'])}
# product_d.update({f'{i}': j for i, j in zip(ppmap['4211033'],ppmap['domain'])})


In [93]:
def save_lookup_to_csv(lookup_dict):
    # Convert the dictionary to a DataFrame
    df = pd.DataFrame(list(lookup_dict.items()), columns=['id', 'name'])
    
    # Save the DataFrame to a CSV file
    df.to_csv('lookup.csv', index=False)

# Your lookup dictionary
lookup_dict = {'90545': 'HP Indigo 1000 Digital Press series', '90547': 'HP Indigo 1000 Digital Press series', '90549': 'HP Indigo 1000 Digital Press series', '3544544': 'HP Indigo 1000 Digital Press series', '3544546': 'HP Indigo 1000 Digital Press series', '2101097052': 'HP Indigo 1000 Digital Press series', '5251493': 'HP Indigo 10000 Digital Press', '5251494': 'HP Indigo 10000 Digital Press', '2100719849': 'HP Indigo 10000 Digital Press', '2100537754': 'HP Indigo 10000 Digital Press', '2100126517': 'HP Indigo 10000 Digital Press', '2100126528': 'HP Indigo 10000 Digital Press', '5251495': 'HP Indigo 10000 Digital Press', '5251497': 'HP Indigo 10000 Digital Press', '2100126518': 'HP Indigo 10000 Digital Press', '2100126529': 'HP Indigo 10000 Digital Press', '34688149': 'HP Indigo 100K Digital Press', '34688150': 'HP Indigo 100K Digital Press', '34688151': 'HP Indigo 100K Digital Press', '34688154': 'HP Indigo 100K Digital Press', '35878165': 'HP Indigo 100K Digital Press', '10799634': 'HP Indigo 12000 Digital Press', '10799635': 'HP Indigo 12000 Digital Press', '2100719850': 'HP Indigo 12000 Digital Press', '2100537735': 'HP Indigo 12000 Digital Press', '10799636': 'HP Indigo 12000 Digital Press', '10902891': 'HP Indigo 12000 Digital Press', '2100537734': 'HP Indigo 12000 Digital Press', '20945895': 'HP Indigo 12000HD Digital Press', '20945896': 'HP Indigo 12000HD Digital Press', '20945899': 'HP Indigo 12000HD Digital Press', '34688174': 'HP Indigo 15K Digital Press', '34688218': 'HP Indigo 15K Digital Press', '34688219': 'HP Indigo 15K Digital Press', '34688222': 'HP Indigo 15K Digital Press', '35865637': 'HP Indigo 15K Digital Press', '35865638': 'HP Indigo 15K Digital Press', '35900353': 'HP Indigo 15K Digital Press', '35865640': 'HP Indigo 15K Digital Press', '3648450': 'HP Indigo s2000 Digital Press', '90556': 'HP Indigo s2000 Digital Press', '90558': 'HP Indigo s2000 Digital Press', '90548': 'HP Indigo s2000 Digital Press', '90560': 'HP Indigo s2000 Digital Press', '90559': 'HP Indigo s2000 Digital Press', '3648449': 'HP Indigo ws2000 Digital Press', '90562': 'HP Indigo ws2000 Digital Press', '90564': 'HP Indigo ws2000 Digital Press', '90563': 'HP Indigo ws2000 Digital Press', '5251498': 'HP Indigo 20000 Digital Press', '5251499': 'HP Indigo 20000 Digital Press', '2100126520': 'HP Indigo 20000 Digital Press', '2100126531': 'HP Indigo 20000 Digital Press', '2100126519': 'HP Indigo 20000 Digital Press', '2100126530': 'HP Indigo 20000 Digital Press', '5251500': 'HP Indigo 20000 Digital Press', '5251502': 'HP Indigo 20000 Digital Press', '37933302': 'HP Indigo 25K Digital Press', '37933303': 'HP Indigo 25K Digital Press', '34688163': 'HP Indigo 25K Digital Press', '34688166': 'HP Indigo 25K Digital Press', '90565': 'HP Indigo 3000 Digital Press Series', '3640220': 'HP Indigo 3000 Digital Press Series', '2100126557': 'HP Indigo 3000 Digital Press Series', '2100126572': 'HP Indigo 3000 Digital Press Series', '2100126556': 'HP Indigo 3000 Digital Press Series', '2100126571': 'HP Indigo 3000 Digital Press Series', '90568': 'HP Indigo 3000 Digital Press Series', '90570': 'HP Indigo 3000 Digital Press Series', '90569': 'HP Indigo 3000 Digital Press Series', '439129': 'HP Indigo 3000 Digital Press Series', '439130': 'HP Indigo 3000 Digital Press Series', '3382251': 'HP Indigo 3500 Digital Press', '3382252': 'HP Indigo 3500 Digital Press', '3382253': 'HP Indigo 3500 Digital Press', '2101097056': 'HP Indigo 3500 Digital Press', '90566': 'HP Indigo w3200 Digital Press Series', '90573': 'HP Indigo w3200 Digital Press Series', '3218087': 'HP Indigo w3200 Digital Press Series', '90575': 'HP Indigo w3200 Digital Press Series', '3223340': 'HP Indigo w3200 Digital Press Series', '3659874': 'HP Indigo w3250 Digital Press', '3244122': 'HP Indigo w3250 Digital Press', '2100126505': 'HP Indigo w3250 Digital Press', '90574': 'HP Indigo w3250 Digital Press', '5251504': 'HP Indigo 30000 Digital Press', '5251518': 'HP Indigo 30000 Digital Press', '2100126521': 'HP Indigo 30000 Digital Press', '2100126532': 'HP Indigo 30000 Digital Press', '5251533': 'HP Indigo 30000 Digital Press', '5251558': 'HP Indigo 30000 Digital Press', '4214301': 'HP Indigo 3550 Digital Press', '4214302': 'HP Indigo 3550 Digital Press', '2100126512': 'HP Indigo 3550 Digital Press', '2100126524': 'HP Indigo 3550 Digital Press', '4214310': 'HP Indigo 3550 Digital Press', '4214316': 'HP Indigo 3550 Digital Press', '37933299': 'HP Indigo 35K Digital Press', '34688157': 'HP Indigo 35K Digital Press', '34688158': 'HP Indigo 35K Digital Press', '34702965': 'HP Indigo 35K Digital Press', '35865641': 'HP Indigo 35K Digital Press', '8954213': 'HP Indigo 3600 Digital Press', '8954214': 'HP Indigo 3600 Digital Press', '8954215': 'HP Indigo 3600 Digital Press', '8693693': 'HP Indigo 3600 Digital Press', '3648452': 'HP Indigo ws4000 Digital Press Series', '3648451': 'HP Indigo ws4000 Digital Press Series', '90705': 'HP Indigo ws4000 Digital Press Series', '90707': 'HP Indigo ws4000 Digital Press Series', '90706': 'HP Indigo ws4000 Digital Press Series', '438409': 'HP Indigo ws4000 Digital Press Series', '7826422': 'HP Indigo ws4000 Digital Press Series', '7826423': 'HP Indigo ws4000 Digital Press Series', '438413': 'HP Indigo ws4000 Digital Press Series', '7826424': 'HP Indigo ws4000 Digital Press Series', '7826426': 'HP Indigo ws4000 Digital Press Series', '7826427': 'HP Indigo ws4000 Digital Press Series', '7826429': 'HP Indigo ws4000 Digital Press Series', '3252083': 'HP Indigo ws4500 Digital Press', '3252084': 'HP Indigo ws4500 Digital Press', '3252085': 'HP Indigo ws4500 Digital Press', '2100126507': 'HP Indigo ws4500 Digital Press', '2101097041': 'HP Indigo ws4500 Digital Press', '3648459': 'HP Indigo 5000 Digital Press series', '383572': 'HP Indigo 5000 Digital Press series', '2100126558': 'HP Indigo 5000 Digital Press series', '2100126573': 'HP Indigo 5000 Digital Press series', '5338467': 'HP Indigo 5000 Digital Press series', '5338468': 'HP Indigo 5000 Digital Press series', '383574': 'HP Indigo 5000 Digital Press series', '5350520': 'HP Indigo 5000 Digital Press series', '383575': 'HP Indigo 5000 Digital Press series', '3382246': 'HP Indigo 5500 Digital Press', '3382247': 'HP Indigo 5500 Digital Press', '3382249': 'HP Indigo 5500 Digital Press', '2101097028': 'HP Indigo 5500 Digital Press', '10902899': 'HP Indigo 50000 Digital Press', '10902900': 'HP Indigo 50000 Digital Press', '10902901': 'HP Indigo 50000 Digital Press', '10902904': 'HP Indigo 50000 Digital Press', '5226271': 'HP Indigo 5600 Digital Press', '5226272': 'HP Indigo 5600 Digital Press', '5226273': 'HP Indigo 5600 Digital Press', '5226275': 'HP Indigo 5600 Digital Press', '2100126513': 'HP Indigo 5600 Digital Press', '10799727': 'HP Indigo 5900 Digital Press', '10799728': 'HP Indigo 5900 Digital Press', '10799729': 'HP Indigo 5900 Digital Press', '10799732': 'HP Indigo 5900 Digital Press', '10902893': 'HP Indigo 5r Digital Press', '10902894': 'HP Indigo 5r Digital Press', '10902895': 'HP Indigo 5r Digital Press', '10902898': 'HP Indigo 5r Digital Press', '18021216': 'HP Indigo 6900 Digital Press', '18021217': 'HP Indigo 6900 Digital Press', '2100719846': 'HP Indigo 6900 Digital Press', '2100537703': 'HP Indigo 6900 Digital Press', '18021218': 'HP Indigo 6900 Digital Press', '18021221': 'HP Indigo 6900 Digital Press', '37933300': 'HP Indigo 6K Digital Press', '37933301': 'HP Indigo 6K Digital Press', '34766689': 'HP Indigo 6K Digital Press', '34766692': 'HP Indigo 6K Digital Press', '2101341287': 'HP Indigo 6K Secure Digital Press series', '2101341290': 'HP Indigo 6K Secure Digital Press series', '2101341301': 'HP Indigo 6K Secure Digital Press series', '2101341317': 'HP Indigo 6K Secure Digital Press series', '10902906': 'HP Indigo 6r Digital Press', '10902907': 'HP Indigo 6r Digital Press', '10902908': 'HP Indigo 6r Digital Press', '10902910': 'HP Indigo 6r Digital Press', '3722855': 'HP Indigo 7000 Digital Press series', '3722856': 'HP Indigo 7000 Digital Press series', '2100126514': 'HP Indigo 7000 Digital Press series', '2100126525': 'HP Indigo 7000 Digital Press series', '3722857': 'HP Indigo 7000 Digital Press series', '3722859': 'HP Indigo 7000 Digital Press series', '2101097032': 'HP Indigo 7000 Digital Press series', '5350521': 'HP Indigo 7000 Digital Press series', '4169552': 'HP Indigo 7500 Digital Press', '4169553': 'HP Indigo 7500 Digital Press', '4169661': 'HP Indigo 7500 Digital Press', '4169663': 'HP Indigo 7500 Digital Press', '5350522': 'HP Indigo 7500 Digital Press', '5226276': 'HP Indigo 7600 Digital Press', '5226277': 'HP Indigo 7600 Digital Press', '2100126515': 'HP Indigo 7600 Digital Press', '2100126526': 'HP Indigo 7600 Digital Press', '5226278': 'HP Indigo 7600 Digital Press', '5226280': 'HP Indigo 7600 Digital Press', '7186479': 'HP Indigo 7800 Digital Press', '7186480': 'HP Indigo 7800 Digital Press', '2100719847': 'HP Indigo 7800 Digital Press', '2100537675': 'HP Indigo 7800 Digital Press', '7186482': 'HP Indigo 7800 Digital Press', '7186484': 'HP Indigo 7800 Digital Press', '2100537674': 'HP Indigo 7800 Digital Press', '10799721': 'HP Indigo 7900 Digital Press', '10799722': 'HP Indigo 7900 Digital Press', '2100719848': 'HP Indigo 7900 Digital Press', '2100537696': 'HP Indigo 7900 Digital Press', '10799723': 'HP Indigo 7900 Digital Press', '10799726': 'HP Indigo 7900 Digital Press', '37933149': 'HP Indigo 7K Digital Press', '37933150': 'HP Indigo 7K Digital Press', '34702961': 'HP Indigo 7K Digital Press', '34702964': 'HP Indigo 7K Digital Press', '11503597': 'HP Indigo 7r Digital Press', '11503704': 'HP Indigo 7r Digital Press', '11503705': 'HP Indigo 7r Digital Press', '11534765': 'HP Indigo 7r Digital Press', '10799628': 'HP Indigo 8000 Digital Press', '10799629': 'HP Indigo 8000 Digital Press', '10799630': 'HP Indigo 8000 Digital Press', '10799633': 'HP Indigo 8000 Digital Press', '37910237': 'HP Indigo 8K Digital Press', '37910238': 'HP Indigo 8K Digital Press', '37921124': 'HP Indigo 8K Digital Press', '37921126': 'HP Indigo 8K Digital Press', '20540618': 'HP Indigo GEM Digital Press series', '20540619': 'HP Indigo GEM Digital Press series', '20540620': 'HP Indigo GEM Digital Press series', '20540624': 'HP Indigo GEM Digital Press series', '33990674': 'HP Indigo Kedem Digital Press series', '33990675': 'HP Indigo Kedem Digital Press series', '33990677': 'HP Indigo Kedem Digital Press series', '33990680': 'HP Indigo Kedem Digital Press series', '2101480396': 'HP Indigo V12 Digital Press', '2101480397': 'HP Indigo V12 Digital Press', '2101480398': 'HP Indigo V12 Digital Press', '2101480399': 'HP Indigo V12 Digital Press', '3919426': 'HP Indigo W7200 Digital Press', '3919427': 'HP Indigo W7200 Digital Press', '3919429': 'HP Indigo W7200 Digital Press', '3919431': 'HP Indigo W7200 Digital Press', '2100537651': 'HP Indigo W7200 Digital Press', '5251478': 'HP Indigo W7250 Digital Press', '5251479': 'HP Indigo W7250 Digital Press', '2100126516': 'HP Indigo W7250 Digital Press', '2100126527': 'HP Indigo W7250 Digital Press', '5251480': 'HP Indigo W7250 Digital Press', '5251482': 'HP Indigo W7250 Digital Press', '2100537669': 'HP Indigo W7250 Digital Press', '5173002': 'HP Indigo WS4600 Digital Press', '5173003': 'HP Indigo WS4600 Digital Press', '5173004': 'HP Indigo WS4600 Digital Press', '5173006': 'HP Indigo WS4600 Digital Press', '3827316': 'HP Indigo WS6000 Digital Press', '3827317': 'HP Indigo WS6000 Digital Press', '3827321': 'HP Indigo WS6000 Digital Press', '3827324': 'HP Indigo WS6000 Digital Press', '2100537647': 'HP Indigo WS6000 Digital Press', '5172997': 'HP Indigo WS6600 Digital Press', '5172998': 'HP Indigo WS6600 Digital Press', '5172999': 'HP Indigo WS6600 Digital Press', '5173001': 'HP Indigo WS6600 Digital Press', '5251488': 'HP Indigo WS6600p Digital Press', '5251489': 'HP Indigo WS6600p Digital Press', '5251490': 'HP Indigo WS6600p Digital Press', '5251492': 'HP Indigo WS6600p Digital Press', '7186486': 'HP Indigo WS6800 Digital Press', '7186487': 'HP Indigo WS6800 Digital Press', '2100719845': 'HP Indigo WS6800 Digital Press', '2100537679': 'HP Indigo WS6800 Digital Press', '7186488': 'HP Indigo WS6800 Digital Press', '7186490': 'HP Indigo WS6800 Digital Press', '10799733': 'HP Indigo WS6800p Digital Press', '10799734': 'HP Indigo WS6800p Digital Press', '10799624': 'HP Indigo WS6800p Digital Press', '10799627': 'HP Indigo WS6800p Digital Press', '3648465': 'Indigo Digital Press E-Print Systems', '90624': 'Indigo Digital Press E-Print Systems', '31592': 'Indigo Digital Press E-Print Systems', '31594': 'Indigo Digital Press E-Print Systems', '90647': 'Indigo Digital Press E-Print Systems', '90648': 'Indigo Digital Press E-Print Systems', '90656': 'Indigo Digital Press E-Print Systems', '90657': 'Indigo Digital Press E-Print Systems', '212612': 'Indigo Digital Press E-Print Systems', '212613': 'Indigo Digital Press E-Print Systems', '212614': 'Indigo Digital Press E-Print Systems', '212615': 'Indigo Digital Press E-Print Systems', '90632': 'Indigo Digital Press E-Print Systems', '90633': 'Indigo Digital Press E-Print Systems', '3648466': 'Indigo Digital Press Omnius Systems', '90680': 'Indigo Digital Press Omnius Systems', '90694': 'Indigo Digital Press Omnius Systems', '90695': 'Indigo Digital Press Omnius Systems', '90682': 'Indigo Digital Press Omnius Systems', '90683': 'Indigo Digital Press Omnius Systems', '3648464': 'Indigo Digital Press Ultrastream Systems', '90616': 'Indigo Digital Press Ultrastream Systems', '91064': 'Indigo Digital Press Ultrastream Systems', '90571': 'Indigo Digital Press Ultrastream Systems', '2101057694': 'HP PageWide Advantage 2200 Series', '2101057742': 'HP PageWide Advantage 2200 Series', '2101057743': 'HP PageWide Advantage 2200 Series', '2101057744': 'HP PageWide Advantage 2200 Series', '2101571612': 'HP PageWide Advantage 2200 Series', '2100469808': 'HP PageWide Advantage 2200 Series', '2101576959': 'HP PageWide Advantage 2200 Series', '2101587198': 'HP PageWide Advantage 2200 Series','8961173': 'HP PageWide T1100 Press series', '8961174': 'HP PageWide T1100 Press series', '8961175': 'HP PageWide T1100 Press series', '8961179': 'HP PageWide T1100 Press series', '26355293': 'HP PageWide T1100 Press series', '26355294': 'HP PageWide T1100 Press series', '21399086': 'HP PageWide T1100 Press series', '19530750': 'HP PageWide T1100 Press series', '22810482': 'HP PageWide T1100 Press series', '22810485': 'HP PageWide T1100 Press series', '22810486': 'HP PageWide T1100 Press series', '27789658': 'HP PageWide T1100 Press series', '2100471738': 'HP PageWide T1100 Press series', '2100251354': 'HP PageWide T1100 Press series', '2101236398': 'HP PageWide T1100 Press series', '2101592556': 'HP PageWide T1100 Press series', '2101592554': 'HP PageWide T1100 Press series', '22810488': 'HP PageWide T1100 Press series', '19390976': 'HP PageWide T400S Press', '7477383': 'HP PageWide T400S Press', '7477384': 'HP PageWide T400S Press', '6531107': 'HP PageWide T400S Press', '9119112': 'HP PageWide T400S Press', '2100546245': 'HP PageWide T400S Press', '2100546246': 'HP PageWide T400S Press', '18280253': 'HP PageWide T400S Press', '22757945': 'HP PageWide T400S Press', '2100251355': 'HP PageWide T400S Press', '2100251356': 'HP PageWide T400S Press', '2101581477': 'HP PageWide T700i Press', '2101581485': 'HP PageWide T700i Press', '2101581486': 'HP PageWide T700i Press', '2101581487': 'HP PageWide T700i Press', '4187448': 'HP PageWide Web Press T200 Color series', '4187449': 'HP PageWide Web Press T200 Color series', '4182637': 'HP PageWide Web Press T200 Color series', '5340337': 'HP PageWide Web Press T200 Color series', '5268269': 'HP PageWide Web Press T200 Color series', '5337565': 'HP PageWide Web Press T200 Color series', '6235341': 'HP PageWide Web Press T200 Color series', '4182871': 'HP PageWide Web Press T200 Color series', '5344649': 'HP PageWide Web Press T230 Color series', '5268266': 'HP PageWide Web Press T230 Color series', '2101604811': 'HP PageWide Web Press T230 Color series', '5268268': 'HP PageWide Web Press T230 Color series', '2100543965': 'HP PageWide Web Press T230 Color series', '7153866': 'HP PageWide Web Press T230 Color series', '5351425': 'HP PageWide Web Press T230 Color series', '21399085': 'HP PageWide Web Press T230 Color series', '21331413': 'HP PageWide Web Press T230 Color series', '24269563': 'HP PageWide Web Press T230 Color series', '10903050': 'HP PageWide Web Press T200 HD series', '10903051': 'HP PageWide Web Press T200 HD series', '15594552': 'HP PageWide Web Press T200 HD series', '15594555': 'HP PageWide Web Press T200 HD series', '10903052': 'HP PageWide Web Press T200 HD series', '20562158': 'HP PageWide Web Press T200 HD series', '24229915': 'HP PageWide Web Press T200 HD series', '2100123028': 'HP PageWide Web Press T200 HD series', '10903112': 'HP PageWide Web Press T200 HD series', '19146640': 'HP PageWide Web Press T200 HD series', '2100564222': 'HP PageWide Web Press T200 HD series', '24229916': 'HP PageWide Web Press T200 HD series', '2100564223': 'HP PageWide Web Press T200 HD series', '26256613': 'HP PageWide Web Press T200 HD series', '38111491': 'HP PageWide Web Press T200 HD series', '2100178024': 'HP PageWide Web Press T200 HD series', '2100178025': 'HP PageWide Web Press T200 HD series', '7296800': 'HP PageWide Web Press T260 Mono', '7296801': 'HP PageWide Web Press T260 Mono', '7296803': 'HP PageWide Web Press T260 Mono', '6302739': 'HP PageWide Web Press T260 Mono', '9119106': 'HP PageWide Web Press T260 Mono', '7267178': 'HP PageWide Web Press T260 Mono', '23510688': 'HP PageWide Web Press T260 Mono', '2100124329': 'HP PageWide Web Press T260 Mono', '23510689': 'HP PageWide Web Press T260 Mono', '24381405': 'HP PageWide Web Press T260 Mono', '2100124492': 'HP PageWide Web Press T260 Mono', '3961028': 'HP PageWide Web Press T300 HD series', '13432070': 'HP PageWide Web Press T300 HD series', '13432072': 'HP PageWide Web Press T300 HD series', '13432075': 'HP PageWide Web Press T300 HD series', '13432077': 'HP PageWide Web Press T300 HD series', '13432080': 'HP PageWide Web Press T300 HD series', '13432083': 'HP PageWide Web Press T300 HD series', '13432086': 'HP PageWide Web Press T300 HD series', '13432088': 'HP PageWide Web Press T300 HD series', '13432091': 'HP PageWide Web Press T300 HD series', '5344779': 'HP PageWide Web Press T300 Mono series', '5337539': 'HP PageWide Web Press T300 Mono series', '5337474': 'HP PageWide Web Press T300 Mono series', '5338959': 'HP PageWide Web Press T300 Mono series', '5337542': 'HP PageWide Web Press T300 Mono series', '9119107': 'HP PageWide Web Press T300 Mono series', '3961029': 'HP PageWide Web Press T300 series', '3961030': 'HP PageWide Web Press T300 series', '5337465': 'HP PageWide Web Press T300 series', '5337522': 'HP PageWide Web Press T300 series', '5337533': 'HP PageWide Web Press T300 series', '5337534': 'HP PageWide Web Press T300 series', '2100542946': 'HP PageWide Web Press T300 series', '5337537': 'HP PageWide Web Press T300 series', '2100542947': 'HP PageWide Web Press T300 series', '5337538': 'HP PageWide Web Press T300 series', '5268270': 'HP PageWide Web Press T300 series', '2100542948': 'HP PageWide Web Press T300 series', '5337568': 'HP PageWide Web Press T300 series', '2100124704': 'HP PageWide Web Press T300 series', '5337551': 'HP PageWide Web Press T300 series', '5337554': 'HP PageWide Web Press T300 series', '5337557': 'HP PageWide Web Press T300 series', '2100124705': 'HP PageWide Web Press T300 series', '5337562': 'HP PageWide Web Press T300 series', '5337468': 'HP PageWide Web Press T300 series', '3961032': 'HP PageWide Web Press T300 series', '5337569': 'HP PageWide Web Press T300 series', '5337572': 'HP PageWide Web Press T300 series', '5337575': 'HP PageWide Web Press T300 series', '5096391': 'HP PageWide Web Press T350', '5096393': 'HP PageWide Web Press T350', '5337582': 'HP PageWide Web Press T350', '5337585': 'HP PageWide Web Press T350', '5268280': 'HP PageWide Web Press T350', '5096396': 'HP PageWide Web Press T350', '5344796': 'HP PageWide Web Press T350M', '5337576': 'HP PageWide Web Press T350M', '5337578': 'HP PageWide Web Press T350M', '9119108': 'HP PageWide Web Press T350M', '5344797': 'HP PageWide Web Press T360', '5268272': 'HP PageWide Web Press T360', '5268274': 'HP PageWide Web Press T360', '9119109': 'HP PageWide Web Press T360', '5096372': 'HP PageWide Web Press T400 Color series', '5096373': 'HP PageWide Web Press T400 Color series', '5096376': 'HP PageWide Web Press T400 Color series', '5337588': 'HP PageWide Web Press T400 Color series', '5337591': 'HP PageWide Web Press T400 Color series', '5268279': 'HP PageWide Web Press T400 Color series', '5337594': 'HP PageWide Web Press T400 Color series', '24829133': 'HP PageWide Web Press T400 Color series', '5337604': 'HP PageWide Web Press T400 Color series', '5096381': 'HP PageWide Web Press T400 Color series', '5337610': 'HP PageWide Web Press T400 Color series', '5344798': 'HP PageWide Web Press T400 Mono series', '5337595': 'HP PageWide Web Press T400 Mono series', '5337597': 'HP PageWide Web Press T400 Mono series', '5337601': 'HP PageWide Web Press T400 Mono series', '9119110': 'HP PageWide Web Press T400 Mono series', '9119111': 'HP PageWide Web Press T400 Mono series', '9713927': 'HP PageWide Web Press T400 Mono series', '9713929': 'HP PageWide Web Press T400 Mono series', '9713930': 'HP PageWide Web Press T400 Mono series', '5344801': 'HP PageWide Web Press T410', '5268275': 'HP PageWide Web Press T410', '5268278': 'HP PageWide Web Press T410', '5337608': 'HP PageWide Web Press T410', '32613967': 'HP PageWide Web Press T410', '2100543987': 'HP PageWide Web Press T410', '5346844': 'HP PageWide Web Press T410', '8961182': 'HP PageWide Web Press T400 HD series', '8961183': 'HP PageWide Web Press T400 HD series', '8961193': 'HP PageWide Web Press T400 HD series', '11145858': 'HP PageWide Web Press T400 HD series', '8961322': 'HP PageWide Web Press T400 HD series', '11145859': 'HP PageWide Web Press T400 HD series', '2100564221': 'HP PageWide Web Press T400 HD series', '2101546336': 'HP PageWide Web Press T400 HD series', '2101546338': 'HP PageWide Web Press T400 HD series', '11145856': 'HP PageWide Web Press T400 HD series', '9068313': 'HP PageWide Web Press T400 HD series', '22757942': 'HP PageWide Web Press T400 HD series', '27789659': 'HP PageWide Web Press T400 HD series', '2101592555': 'HP PageWide Web Press T400 HD series', '11145860': 'HP PageWide Web Press T400 HD series', '9068312': 'HP PageWide Web Press T400 HD series', '34104723': 'HP PageWide Web Press T400 HD series', '2100088957': 'HP PageWide Web Press T400 HD series'}

# Save the lookup dictionary to a CSV file
save_lookup_to_csv(lookup_dict)

In [97]:
import pandas as pd

def save_domain_map_to_csv(domain_map):
    # Convert the dictionary to a DataFrame and ensure IDs are strings
    df = pd.DataFrame(list(domain_map.items()), columns=['product_id', 'domain'])
    df['product_id'] = df['product_id'].astype(str)
    
    # Save the DataFrame to a CSV file
    df.to_csv('kaas_domain_map.csv', index=False)

# Your domain map dictionary
domain_map = {
'90545': 'Indigo', '90547': 'Indigo', '90549': 'Indigo', '3544544': 'Indigo', '3544546': 'Indigo', '2101097052': 'Indigo', '5251493': 'Indigo', '5251494': 'Indigo', '2100719849': 'Indigo', '2100537754': 'Indigo', '2100126517': 'Indigo', '2100126528': 'Indigo', '5251495': 'Indigo', '5251497': 'Indigo', '2100126518': 'Indigo', '2100126529': 'Indigo', '34688149': 'Indigo', '34688150': 'Indigo', '34688151': 'Indigo', '34688154': 'Indigo', '35878165': 'Indigo', '10799634': 'Indigo', '10799635': 'Indigo', '2100719850': 'Indigo', '2100537735': 'Indigo', '10799636': 'Indigo', '10902891': 'Indigo', '2100537734': 'Indigo', '20945895': 'Indigo', '20945896': 'Indigo', '20945899': 'Indigo', '34688174': 'Indigo', '34688218': 'Indigo', '34688219': 'Indigo', '34688222': 'Indigo', '35865637': 'Indigo', '35865638': 'Indigo', '35900353': 'Indigo', '35865640': 'Indigo', '3648450': 'Indigo', '90556': 'Indigo', '90558': 'Indigo', '90548': 'Indigo', '90560': 'Indigo', '90559': 'Indigo', '3648449': 'Indigo', '90562': 'Indigo', '90564': 'Indigo', '90563': 'Indigo', '5251498': 'Indigo', '5251499': 'Indigo', '2100126520': 'Indigo', '2100126531': 'Indigo', '2100126519': 'Indigo', '2100126530': 'Indigo', '5251500': 'Indigo', '5251502': 'Indigo', '37933302': 'Indigo', '37933303': 'Indigo', '34688163': 'Indigo', '34688166': 'Indigo', '90565': 'Indigo', '3640220': 'Indigo', '2100126557': 'Indigo', '2100126572': 'Indigo', '2100126556': 'Indigo', '2100126571': 'Indigo', '90568': 'Indigo', '90570': 'Indigo', '90569': 'Indigo', '439129': 'Indigo', '439130': 'Indigo', '3382251': 'Indigo', '3382252': 'Indigo', '3382253': 'Indigo', '2101097056': 'Indigo', '90566': 'Indigo', '90573': 'Indigo', '3218087': 'Indigo', '90575': 'Indigo', '3223340': 'Indigo', '3659874': 'Indigo', '3244122': 'Indigo', '2100126505': 'Indigo', '90574': 'Indigo', '5251504': 'Indigo', '5251518': 'Indigo', '2100126521': 'Indigo', '2100126532': 'Indigo', '5251533': 'Indigo', '5251558': 'Indigo', '4214301': 'Indigo', '4214302': 'Indigo', '2100126512': 'Indigo', '2100126524': 'Indigo', '4214310': 'Indigo', '4214316': 'Indigo', '37933299': 'Indigo', '34688157': 'Indigo', '34688158': 'Indigo', '34702965': 'Indigo', '35865641': 'Indigo', '8954213': 'Indigo', '8954214': 'Indigo', '8954215': 'Indigo', '8693693': 'Indigo', '3648452': 'Indigo', '3648451': 'Indigo', '90705': 'Indigo', '90707': 'Indigo', '90706': 'Indigo', '438409': 'Indigo', '7826422': 'Indigo', '7826423': 'Indigo', '438413': 'Indigo', '7826424': 'Indigo', '7826426': 'Indigo', '7826427': 'Indigo', '7826429': 'Indigo', '3252083': 'Indigo', '3252084': 'Indigo', '3252085': 'Indigo', '2100126507': 'Indigo', '2101097041': 'Indigo', '3648459': 'Indigo', '383572': 'Indigo', '2100126558': 'Indigo', '2100126573': 'Indigo', '5338467': 'Indigo', '5338468': 'Indigo', '383574': 'Indigo', '5350520': 'Indigo', '383575': 'Indigo', '3382246': 'Indigo', '3382247': 'Indigo', '3382249': 'Indigo', '2101097028': 'Indigo', '10902899': 'Indigo', '10902900': 'Indigo', '10902901': 'Indigo', '10902904': 'Indigo', '5226271': 'Indigo', '5226272': 'Indigo', '5226273': 'Indigo', '5226275': 'Indigo', '2100126513': 'Indigo', '10799727': 'Indigo', '10799728': 'Indigo', '10799729': 'Indigo', '10799732': 'Indigo', '10902893': 'Indigo', '10902894': 'Indigo', '10902895': 'Indigo', '10902898': 'Indigo', '18021216': 'Indigo', '18021217': 'Indigo', '2100719846': 'Indigo', '2100537703': 'Indigo', '18021218': 'Indigo', '18021221': 'Indigo', '37933300': 'Indigo', '37933301': 'Indigo', '34766689': 'Indigo', '34766692': 'Indigo', '2101341287': 'Indigo', '2101341290': 'Indigo', '2101341301': 'Indigo', '2101341317': 'Indigo', '10902906': 'Indigo', '10902907': 'Indigo', '10902908': 'Indigo', '10902910': 'Indigo', '3722855': 'Indigo', '3722856': 'Indigo', '2100126514': 'Indigo', '2100126525': 'Indigo', '3722857': 'Indigo', '3722859': 'Indigo', '2101097032': 'Indigo', '5350521': 'Indigo', '4169552': 'Indigo', '4169553': 'Indigo', '4169661': 'Indigo', '4169663': 'Indigo', '5350522': 'Indigo', '5226276': 'Indigo', '5226277': 'Indigo', '2100126515': 'Indigo', '2100126526': 'Indigo', '5226278': 'Indigo', '5226280': 'Indigo', '7186479': 'Indigo', '7186480': 'Indigo', '2100719847': 'Indigo', '2100537675': 'Indigo', '7186482': 'Indigo', '7186484': 'Indigo', '2100537674': 'Indigo', '10799721': 'Indigo', '10799722': 'Indigo', '2100719848': 'Indigo', '2100537696': 'Indigo', '10799723': 'Indigo', '10799726': 'Indigo', '37933149': 'Indigo', '37933150': 'Indigo', '34702961': 'Indigo', '34702964': 'Indigo', '11503597': 'Indigo', '11503704': 'Indigo', '11503705': 'Indigo', '11534765': 'Indigo', '10799628': 'Indigo', '10799629': 'Indigo', '10799630': 'Indigo', '10799633': 'Indigo', '37910237': 'Indigo', '37910238': 'Indigo', '37921124': 'Indigo', '37921126': 'Indigo', '20540618': 'Indigo', '20540619': 'Indigo', '20540620': 'Indigo', '20540624': 'Indigo', '33990674': 'Indigo', '33990675': 'Indigo', '33990677': 'Indigo', '33990680': 'Indigo', '2101480396': 'Indigo', '2101480397': 'Indigo', '2101480398': 'Indigo', '2101480399': 'Indigo', '3919426': 'Indigo', '3919427': 'Indigo', '3919429': 'Indigo', '3919431': 'Indigo', '2100537651': 'Indigo', '5251478': 'Indigo', '5251479': 'Indigo', '2100126516': 'Indigo', '2100126527': 'Indigo', '5251480': 'Indigo', '5251482': 'Indigo', '2100537669': 'Indigo', '5173002': 'Indigo', '5173003': 'Indigo', '5173004': 'Indigo', '5173006': 'Indigo', '3827316': 'Indigo', '3827317': 'Indigo', '3827321': 'Indigo', '3827324': 'Indigo', '2100537647': 'Indigo', '5172997': 'Indigo', '5172998': 'Indigo', '5172999': 'Indigo', '5173001': 'Indigo', '5251488': 'Indigo', '5251489': 'Indigo', '5251490': 'Indigo', '5251492': 'Indigo', '7186486': 'Indigo', '7186487': 'Indigo', '2100719845': 'Indigo', '2100537679': 'Indigo', '7186488': 'Indigo', '7186490': 'Indigo', '10799733': 'Indigo', '10799734': 'Indigo', '10799624': 'Indigo', '10799627': 'Indigo', '3648465': 'Indigo', '90624': 'Indigo', '31592': 'Indigo', '31594': 'Indigo', '90647': 'Indigo', '90648': 'Indigo', '90656': 'Indigo', '90657': 'Indigo', '212612': 'Indigo', '212613': 'Indigo', '212614': 'Indigo', '212615': 'Indigo', '90632': 'Indigo', '90633': 'Indigo', '3648466': 'Indigo', '90680': 'Indigo', '90694': 'Indigo', '90695': 'Indigo', '90682': 'Indigo', '90683': 'Indigo', '3648464': 'Indigo', '90616': 'Indigo', '91064': 'Indigo', '90571': 'Indigo', '2101057694': 'PWP', '2101057742': 'PWP', '2101057743': 'PWP', '2101057744': 'PWP', '2101571612': 'PWP', '2100469808': 'PWP', '2101576959': 'PWP', '2101587198': 'PWP','8961173': 'PWP', '8961174': 'PWP', '8961175': 'PWP', '8961179': 'PWP', '26355293': 'PWP', '26355294': 'PWP', '21399086': 'PWP', '19530750': 'PWP', '22810482': 'PWP', '22810485': 'PWP', '22810486': 'PWP', '27789658': 'PWP', '2100471738': 'PWP', '2100251354': 'PWP', '2101236398': 'PWP', '2101592556': 'PWP', '2101592554': 'PWP', '22810488': 'PWP', '19390976': 'PWP', '7477383': 'PWP', '7477384': 'PWP', '6531107': 'PWP', '9119112': 'PWP', '2100546245': 'PWP', '2100546246': 'PWP', '18280253': 'PWP', '22757945': 'PWP', '2100251355': 'PWP', '2100251356': 'PWP', '2101581477': 'PWP', '2101581485': 'PWP', '2101581486': 'PWP', '2101581487': 'PWP', '4187448': 'PWP', '4187449': 'PWP', '4182637': 'PWP', '5340337': 'PWP', '5268269': 'PWP', '5337565': 'PWP', '6235341': 'PWP', '4182871': 'PWP', '5344649': 'PWP', '5268266': 'PWP', '2101604811': 'PWP', '5268268': 'PWP', '2100543965': 'PWP', '7153866': 'PWP', '5351425': 'PWP', '21399085': 'PWP', '21331413': 'PWP', '24269563': 'PWP', '10903050': 'PWP', '10903051': 'PWP', '15594552': 'PWP', '15594555': 'PWP', '10903052': 'PWP', '20562158': 'PWP', '24229915': 'PWP', '2100123028': 'PWP', '10903112': 'PWP', '19146640': 'PWP', '2100564222': 'PWP', '24229916': 'PWP', '2100564223': 'PWP', '26256613': 'PWP', '38111491': 'PWP', '2100178024': 'PWP', '2100178025': 'PWP', '7296800': 'PWP', '7296801': 'PWP', '7296803': 'PWP', '6302739': 'PWP', '9119106': 'PWP', '7267178': 'PWP', '23510688': 'PWP', '2100124329': 'PWP', '23510689': 'PWP', '24381405': 'PWP', '2100124492': 'PWP', '3961028': 'PWP', '13432070': 'PWP', '13432072': 'PWP', '13432075': 'PWP', '13432077': 'PWP', '13432080': 'PWP', '13432083': 'PWP', '13432086': 'PWP', '13432088': 'PWP', '13432091': 'PWP', '5344779': 'PWP', '5337539': 'PWP', '5337474': 'PWP', '5338959': 'PWP', '5337542': 'PWP', '9119107': 'PWP', '3961029': 'PWP', '3961030': 'PWP', '5337465': 'PWP', '5337522': 'PWP', '5337533': 'PWP', '5337534': 'PWP', '2100542946': 'PWP', '5337537': 'PWP', '2100542947': 'PWP', '5337538': 'PWP', '5268270': 'PWP', '2100542948': 'PWP', '5337568': 'PWP', '2100124704': 'PWP', '5337551': 'PWP', '5337554': 'PWP', '5337557': 'PWP', '2100124705': 'PWP', '5337562': 'PWP', '5337468': 'PWP', '3961032': 'PWP', '5337569': 'PWP', '5337572': 'PWP', '5337575': 'PWP', '5096391': 'PWP', '5096393': 'PWP', '5337582': 'PWP', '5337585': 'PWP', '5268280': 'PWP', '5096396': 'PWP', '5344796': 'PWP', '5337576': 'PWP', '5337578': 'PWP', '9119108': 'PWP', '5344797': 'PWP', '5268272': 'PWP', '5268274': 'PWP', '9119109': 'PWP', '5096372': 'PWP', '5096373': 'PWP', '5096376': 'PWP', '5337588': 'PWP', '5337591': 'PWP', '5268279': 'PWP', '5337594': 'PWP', '24829133': 'PWP', '5337604': 'PWP', '5096381': 'PWP', '5337610': 'PWP', '5344798': 'PWP', '5337595': 'PWP', '5337597': 'PWP', '5337601': 'PWP', '9119110': 'PWP', '9119111': 'PWP', '9713927': 'PWP', '9713929': 'PWP', '9713930': 'PWP', '5344801': 'PWP', '5268275': 'PWP', '5268278': 'PWP', '5337608': 'PWP', '32613967': 'PWP', '2100543987': 'PWP', '5346844': 'PWP', '8961182': 'PWP', '8961183': 'PWP', '8961193': 'PWP', '11145858': 'PWP', '8961322': 'PWP', '11145859': 'PWP', '2100564221': 'PWP', '2101546336': 'PWP', '2101546338': 'PWP', '11145856': 'PWP', '9068313': 'PWP', '22757942': 'PWP', '27789659': 'PWP', '2101592555': 'PWP', '11145860': 'PWP', '9068312': 'PWP', '34104723': 'PWP', '2100088957': 'PWP'
}

# Save the domain map dictionary to a CSV file
save_domain_map_to_csv(domain_map)


In [193]:
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.max_rows', None)     # Show all rows
pd.set_option('display.width', 1000)        # Set the display width to a larger number
pd.set_option('display.max_colwidth', None) # Show full content of each column

In [78]:
product_names=[i for i in ipmap['level3'].dropna()]
product_names.extend([i for i in ppmap['level3'].dropna()])

In [287]:
common=[]
for i in kz_prod:
    if i in product_names:
        common.append(i)

In [173]:
kaas_source=df1['documentID'].to_list()

In [17]:
from opensearchpy.helpers import scan
from opensearchpy import OpenSearch, helpers
class OpenSearchManager:
    config1=OpenSearchConnectConfigStg()
    client = OpenSearch(
                hosts=[{'host': config1.host, 'port': config1.port}],
                http_compress=True,
                http_auth=config1.auth,
                use_ssl=config1.use_ssl,
                verify_certs=config1.verify_certs
            )
    @staticmethod
    def fetch_and_update_missing_documents(index_name, document_id_series):
        documents_to_update = []
        query = {
            "query": {
                "match_all": {}
            }
        }

        # Fetch all documents from the index
        results = scan(OpenSearchManager.client, query=query, index=index_name)

        # Extract the document IDs from the DataFrame for comparison
        df_document_ids = document_id_series.astype(str).tolist()

        # Iterate over the fetched results
        for res in results:
            # If the documentID is not found in the DataFrame, mark it as 'rejected'
            if res['_id'] not in df_document_ids:
                # Remove the 'query_embedding' field if it exists
                res['_source'].pop('query_embedding', None)
                res['_source']['Doc_Status'] = 'deleted'
                documents_to_update.append(res)

        # Prepare the documents for bulk update
        actions = [
            {
                "_op_type": "update",
                "_index": index_name,
                "_id": doc['_id'],
                "doc": doc['_source']
            }
            for doc in documents_to_update
        ]

        # Perform the bulk update
        helpers.bulk(OpenSearchManager.client, actions)

        return f"{len(documents_to_update)} documents updated with 'deleted' in Doc_Status and 'query_embedding' removed in index '{index_name}'"

    @staticmethod
    def clean_dashboard_data(index_name,source):
        # index_name='data_quality_check_iteration'
        # source='kaas'
        query = {
            "query": {
                "match_all": {}
            }
        }
        results = scan(OpenSearchManager.client, query=query, index=index_name)
        test = [res['_source'] for res in results]
        cd_df = pd.DataFrame(test)
        cd_df = cd_df[cd_df['Source'] == source]
        
        # Identify unmatched records
        df_document_ids = set(test_df['documentID'].astype(str).tolist())
        cd_df['documentID'] = cd_df['documentID'].astype(str)
        
        # Records in cd_df but not in test_df
        unmatched_records = cd_df[~cd_df['documentID'].isin(df_document_ids)]
        actions = [
            {
                "_op_type": "update",
                "_index": index_name,
                "_id": row['documentID'],
                "doc": {
                    "Doc_Status": "deleted"
                }
            }
            for _, row in unmatched_records.iterrows()
        ]
        
        # Execute the bulk update
        if actions:
            helpers.bulk(OpenSearchManager.client, actions)
        return f"{len(actions)} documents updated with 'deleted' in Doc_Status in index '{index_name}'"
    @staticmethod
    def fetch_all_documents(index_name):
        """Fetches all documents from the specified index."""
        query = {"query": {"match_all": {}}}
        results = scan(OpenSearchManager.client, query=query, index=index_name)
        return results
        
    @staticmethod
    def process_and_delete_records(index_name):
        """Fetches, filters, and deletes records with Doc_Status 'deleted'."""
        results = OpenSearchManager.fetch_all_documents(index_name)
        actions = []

        for record in results:
            if record["_source"].get("Doc_Status") == "deleted":
                actions.append(
                    {"_op_type": "delete", "_index": index_name, "_id": record["_id"]}
                )

        if actions:
            bulk(OpenSearchManager.client, actions)
            return f"{len(actions)} documents deleted in '{index_name}'"

C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\opensearchpy\connection\http_urllib3.py:208: UserWarning: Connecting to https://vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com:443 using SSL with verify_certs=False is insecure.
  warnings.warn(


In [34]:
import time
start_time = time.time()
print(OpenSearchManager.fetch_and_update_missing_documents('kaas.v5.dev', df1['documentID']))
end_time=time.time()
print('time_taken',end_time-start_time)

C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghr

13 documents updated with 'deleted' in Doc_Status and 'query_embedding' removed in index 'kaas.v5.dev'
time_taken 8.814879417419434


In [35]:
import time
start_time = time.time()
print(OpenSearchManager.clean_dashboard_data('data_quality_check_iteration', 'kaas'))
end_time=time.time()
print('time_taken',end_time-start_time)

C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghrejqchy.us-west-2.es.amazonaws.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
C:\Users\KuBP064\AppData\Local\anaconda3\Lib\site-packages\urllib3\connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'vpc-ks-stage-opensearch-es-a6nqrfnukskuiliztghr

13 documents updated with 'deleted' in Doc_Status in index 'data_quality_check_iteration'
time_taken 8.582924365997314


In [18]:
l=[]
for i in df1['documentID']:
    l.append(i)


In [19]:
def get_encrypted_token(doc_id):
    # Define the URL
    url = "https://css.api.hp.com/knowledge/v2/generateEncryptedToken"

    # Get the access token
    access_token = get_access_token()

    # Define the header
    headers = {
        "Authorization": "Bearer " + access_token,
    }

    # Define the body
    body = {
        "accessToken": "Bearer " + access_token,
        "docId": doc_id
    }

    # Send the POST request
    response = requests.post(url, headers=headers, json=body)
    response = response.json()
    encrypted_token = response['encryptedToken']
   
    data_url = f"https://css.api.hp.com/knowledge/v2/render/{encrypted_token}/{doc_id}"
    return data_url

# Example usage:
doc_id = "ish_9160795-9160647-16"

url = get_encrypted_token(doc_id)
url


'https://css.api.hp.com/knowledge/v2/render/6f9MBfc6nzTbDR+2Kbx6SyksvNHvi4fIarpLjO3hb3Q_hEJqA_dSTf48NoctmBGAobq52ZCGK3SZtmPHYBNAYa+q9ozEQtOdq9l6Xugo6Cj7of1BG1QLRIg0HG559CAjr7Dm2K6xTdlcMscvXv45DVk5pF6aLHiIPOo1xE88yfB+XnP4lImwlyVoZqZ1VjqtCqC_rhjsghIE_gxFTxaxWhF3mZY+1Hkno66EQm8V4wB0p+eTYgioP_aY4KpKcnPWigGCj2f6eZ6lDarptT784s8mjeewtsMv3XOmK_L_RNbuLhSkHu+pEKddViEgNaX23znzDYtAPfR2ZN2uDhKkxjNzwqbRJ3X2i_dds4WZXH+HtEpFfZreG3A_S4nWCBIYTo8MyOy02ZCYz49XiocoZz8erb_lYo5c33pJOx9HDJ0YxY_MxteHOEgOMQq3PU8mmCFrAdyyody6UKX8RvCBA7SEy+zVQEeqfVkY9a+JXhaYA9zAFreuVC1WS1WMgtoukV4uQgu_T1HQVMT6c4q8aeg1Au1UFJcHVyGH19nbycBIG8ADjlx7WMpxnSmofKpVY86DNDUEaiI8QOCdQubmZ9j+ZxSjdOO_EofDvJYIJ8mJRPzlJ1YRMTXUWqHUfDPXNK17jnKH4zw7FQKGLe4VhgY77T70jAQukHZsdkFGehsuyA4xCYFi3OPaMiOgHaBcR7UIJyOCC1FePBIl7eqfYAe6BHiSRFL6l1lUwg1Ds8jS5kAOzL_nNefBCT3fM93JvZwNOmmGKeyhjJtCty62lNkq0xXV5gVtEAJaAtsSTdNhOgR9+HITIF85V7rTr6WOt_ZMRJn5+_zw215oT6IjB3Sasuv9_q+gLn7lC1VEqvtalSKPVKMwC7cKiitatHegNOY7qzxSSVsnATJcmLYGsBRIyZYgYzQvetvmWwloQkiN6Aq5Sx8suBQQSbDk

In [23]:
def get_bulk_render_url(documentIDs):
    
    bulk_render_url='https://css.api.hp.com/knowledge/v2/getRenderLinks'
    access_token = get_access_token()
        
    headers = {
        "Content-Type": "application/json",
        "Authorization": "Bearer " + access_token,
    }
    
    data = {
        "languageCode": 'en',
        "requests": [
            {
                "languageCode": 'en',
                "ids": documentIDs,
            },
        ],
    }
    
    response = requests.post(
        bulk_render_url, headers=headers, json=data
    )
    response.raise_for_status()
    response = response.json()
    data=response[0]['renderLinks']
    # print(data[0])
    renderlinks = [i['renderLink'] for i in data if 'renderLink' in i]
    failed_count = sum(1 for i in data if i.get('status') == 'FAILURE')
    success_count = sum(1 for i in data if i.get('status') == 'SUCCESS')
    # print(success_count,failed_count)
    return renderlinks

doc=['pdf_3999714_en-US-6']
url = get_bulk_render_url(doc)
url

['https://kaas.hpcloud.hp.com/pdf-nonpublic/pdf_3999714_en-US-6.pdf?Expires=1728298827&Signature=bT4L-q5Ca96X7EYAAnrwNxFh2cyJZSzZiF51MHU4QrVLkHemZbr~drNVu0PNITEb82ha-HDJHmCH4P2hLBCyshYKiltF9YbwJN1uqxIQ0T0HZNIez7Wl5lfUg-GvKD~Shz3Sm2Nm6Q4jvBmfzfwtuJKkidvU3aHteNj71mRMiO-HOE2z9YJhyIChxu0WkXGFUxqyUttcRwcLa1Z~dy0~v7UQPiz4flBlKNxSO8xRurS~fHMsFTR5CYv7A~BmbwQ~meIxTnOPSuTQNLZ1NP9k2Y9XKSE3i4GeQtOfLIKlxaQ-F1Wjh2yCWJZn9ma-VVzVDev783-NLqvtTMwRfieuXw__&Key-Pair-Id=APKAIEP4ZT2OPKULVJXQ']

In [45]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

# Function to clean the text
def clean_text(text):
    return ' '.join(text.split())

def get_encrypted_token(doc_id):
    # Define the URL
    url = "https://css.api.hp.com/knowledge/v2/generateEncryptedToken"

    # Get the access token
    access_token = get_access_token()

    # Define the header
    headers = {
        "Authorization": "Bearer " + access_token,
    }

    # Define the body
    body = {
        "accessToken": "Bearer " + access_token,
        "docId": doc_id
    }

    # Send the POST request
    response = requests.post(url, headers=headers, json=body)
    response = response.json()
    encrypted_token = response['encryptedToken']
   
    data_url = f"https://css.api.hp.com/knowledge/v2/render/{encrypted_token}/{doc_id}"
    return data_url

# Function to recursively extract text from paragraphs and headlines
def extract_content(soup):
    content = []
    for tag in soup.find_all(['p', 'h1', 'h2', 'h3', 'h4', 'h5', 'h6']):
        text = clean_text(tag.get_text())
        if text:
            content.append(text)
    return content

data = []
for doc_id in l:  # Loop through the first 10 document IDs
    url = get_encrypted_token(doc_id)  # Fetch the URL using the encrypted token
    page = requests.get(url)  # Retrieve the page content
    html_content = page.content  # Directly store the HTML content in memory
    
    # Parse the HTML content using BeautifulSoup
    soup = BeautifulSoup(html_content, 'html.parser')
    
    # Extract text from paragraphs, headlines, etc.
    content = extract_content(soup)
    
    # Clean the extracted data
    all_content = '\n'.join(content)
    
    # Append the documentID and content to the list
    data.append({'documentID': doc_id, 'Content': all_content})

# Create a DataFrame from the collected data
df3 = pd.DataFrame(data)

In [54]:
# get all html tags
def clean_text(text):
    return ' '.join(text.split())

# Function to extract all tags in the HTML document
def extract_all_tags(soup):
    tags = set()  # To store unique tag names
    for tag in soup.find_all(True):  # True matches all tags
        tags.add(tag.name)
    return tags

data = []
all_unique_tags = set()  # To collect unique tags across all documents

for doc_id in l[1:2]:
    url = get_encrypted_token(doc_id)
    page = requests.get(url)
    html_content = page.content
    
    # Parse the HTML content using BeautifulSoup
    soup = BeautifulSoup(html_content, 'html.parser')
    
    # Collect unique tags from the document
    tags_in_doc = extract_all_tags(soup)
    all_unique_tags.update(tags_in_doc)  # Add unique tags to the global set

# After processing all documents, print the unique tags found
print("Unique tags in the data:", all_unique_tags)

Unique tags in the data: {'th', 'div', 'thead', 'p', 'tbody', 'h1', 'table', 'tr', 'col', 'td', 'strong'}


In [99]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from concurrent.futures import ThreadPoolExecutor, as_completed

# Function to clean the text
def clean_text(text):
    return ' '.join(text.split())

# Function to fetch the encrypted token
def get_encrypted_token(doc_id):
    url = "https://css.api.hp.com/knowledge/v2/generateEncryptedToken"
    access_token = get_access_token()

    headers = {
        "Authorization": "Bearer " + access_token,
    }

    body = {
        "accessToken": "Bearer " + access_token,
        "docId": doc_id
    }

    response = requests.post(url, headers=headers, json=body).json()
    encrypted_token = response['encryptedToken']
    
    # Generate the data URL
    data_url = f"https://css.api.hp.com/knowledge/v2/render/{encrypted_token}/{doc_id}"
    return data_url

# Function to recursively extract text from paragraphs and headlines
def extract_content(soup):
    content = []
    for tag in soup.find_all(['p', 'h1', 'h2', 'h3', 'h4', 'h5', 'h6']):
        text = clean_text(tag.get_text())
        if text:
            content.append(text)
    return content

# Function to fetch and parse content for a given document ID
def fetch_document_content(doc_id):
    try:
        url = get_encrypted_token(doc_id)  # Fetch the URL using the encrypted token
        page = requests.get(url)  # Retrieve the page content
        html_content = page.content  # Directly store the HTML content in memory
        
        # Parse the HTML content using BeautifulSoup
        soup = BeautifulSoup(html_content, 'html.parser')
        
        # Extract text from paragraphs, headlines, etc.
        content = extract_content(soup)
        
        # Clean the extracted data
        all_content = '\n'.join(content)
        
        # Return the document ID and content
        return {'documentID': doc_id, 'Content': all_content}
    except Exception as e:
        print(f"Error processing document ID {doc_id}: {e}")
        return None

# Function to run multithreading and gather results
def process_documents_in_parallel(doc_ids, max_workers=10):
    data = []
    
    # Use ThreadPoolExecutor for parallel processing
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        # Submit tasks to the executor
        futures = {executor.submit(fetch_document_content, doc_id): doc_id for doc_id in doc_ids}
        
        # Gather results as they are completed
        for future in as_completed(futures):
            result = future.result()
            if result:
                data.append(result)
    
    return data

# Sample list of document IDs
doc_ids = l1  # Assuming `l` is a list of document IDs

# Process documents in parallel
data = process_documents_in_parallel(doc_ids, max_workers=20)

# Create a DataFrame from the collected data
df4 = pd.DataFrame(data)


In [13]:
# html processing with single render link
import requests
import time
from bs4 import BeautifulSoup
import pandas as pd
from concurrent.futures import ThreadPoolExecutor, as_completed
print(time.time())
# Function to clean the text
def clean_text(text):
    return ' '.join(text.split())

# Function to fetch the encrypted token
def get_encrypted_token(doc_id):
    url = "https://css.api.hp.com/knowledge/v2/generateEncryptedToken"
    access_token = get_access_token()

    headers = {
        "Authorization": "Bearer " + access_token,
    }

    body = {
        "accessToken": "Bearer " + access_token,
        "docId": doc_id
    }

    response = requests.post(url, headers=headers, json=body).json()
    encrypted_token = response['encryptedToken']
    
    # Generate the data URL
    data_url = f"https://css.api.hp.com/knowledge/v2/render/{encrypted_token}/{doc_id}"
    return data_url

# Function to recursively extract text from paragraphs and headlines
def extract_content(soup):
    content = []
    for tag in soup.find_all(['p', 'h1', 'h2', 'h3', 'h4', 'h5', 'h6']):
        text = clean_text(tag.get_text())
        if text:
            content.append(text)
    return content

# Function to fetch and parse content for a given record (row from DataFrame)
def fetch_document_content(row):
    try:
        doc_id = row['documentID']  # Extract documentID from the row
        url = get_encrypted_token(doc_id)  # Fetch the URL using the encrypted token
        page = requests.get(url)  # Retrieve the page content
        html_content = page.content  # Directly store the HTML content in memory
        
        # Parse the HTML content using BeautifulSoup
        soup = BeautifulSoup(html_content, 'html.parser')
        
        # Extract text from paragraphs, headlines, etc.
        content = extract_content(soup)
        
        # Clean the extracted data
        all_content = '\n'.join(content)
        
        # Return the document metadata and content
        return {'metadata': row.to_dict(), 'text': all_content}
    except Exception as e:
        print(f"Error processing document ID {row['documentID']}: {e}")
        return {'metadata': row.to_dict(), 'text': None}

# Function to run multithreading and gather results
def process_documents_in_parallel(df, max_workers=10):
    data = []
    
    # Use ThreadPoolExecutor for parallel processing
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        # Submit tasks to the executor for each row in the DataFrame
        futures = {executor.submit(fetch_document_content, row): row['documentID'] for _, row in df.iterrows()}
        
        # Gather results as they are completed
        for future in as_completed(futures):
            result = future.result()
            if result:
                data.append(result)
    
    return data

# Process documents in parallel
data = process_documents_in_parallel(df1, max_workers=20)

# Create a new DataFrame from the collected data with 'metadata' and 'text' columns
df_result = pd.DataFrame(data)

print(time.time())

1727696213.3103402
Error processing document ID pdf_9071274_en-US-4: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_8674677_en-US-4: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_8726858_en-US-4: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_9295561_en-US-6: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_10474408_en-US-6: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_9195432_en-US-6: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_10494220_en-US-6: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_9196216_en-US-6: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_10481311_en-US-6: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_10485492_en-US-6: Expecting value: line 1 column 1 (char 0)
Error processing document ID pdf_10575418_en-US-6: Expect

In [15]:
df_result['metadata']=df_result['metadata'].apply(lambda x: {**x, 'page_number': 0})

In [16]:
df_result.to_dict(orient='records')[0]

{'metadata': {'documentID': 'ish_9053442-8640264-16',
  'title': 'Replacing the duplex conveyor suction cups',
  'contentTypeHeader': 'Product Support',
  'renderLink': None,
  'matchScore': 7.106933,
  'description': 'Do this procedure every 2,000,000 sheets, according to the press counter.',
  'contentUpdateDate': '2023-06-22 05:57:41',
  'language': 'en',
  'disclosureLevel': '287477763180518087286275037723076',
  'contentType': 'How To (Printing and Imaging)',
  'store': 'Product Documents',
  'docSource': 'UDP',
  'ishType': 'Topic',
  'hpID': 'N/A',
  'technicalLevel': 'User Basic',
  'position': 50,
  'parentDoc': 'pdf_8674677_en-US-4.pdf',
  'ti_desc_prod': 'Replacing the duplex conveyor suction cups Do this procedure every 2,000,000 sheets, according to the press counter. ish_9053442-8640264-16',
  'Doc_Status': 'published',
  'Domain': 'Indigo',
  'products': ['HP Indigo 10000 Digital Press'],
  'persona': 'Operator',
  'page_number': 0},
 'text': 'Replacing the duplex convey

In [41]:
# parallel processing send to opensearch
from langchain.schema import Document
from concurrent.futures import ThreadPoolExecutor, as_completed
from langchain.schema import Document
import os
from typing import List
import pymupdf4llm
from chromadb import EmbeddingFunction, Documents
from langchain.vectorstores import elasticsearch
#from chromadb import EmbeddingFunction, Documents, Embeddings
from langchain_community.document_loaders import PyPDFLoader
from langchain_community.retrievers import ElasticSearchBM25Retriever
from langchain_community.vectorstores import OpenSearchVectorSearch, Chroma
from langchain_text_splitters import MarkdownHeaderTextSplitter
from openai import OpenAI
import requests
from typing import List
from langchain_core.embeddings import Embeddings
# Function to send documents to OpenSearch in parallel
def send_chunk_to_opensearch(df_chunk):
    try:
        documents = [
            Document(page_content=row['text'], metadata=row['metadata'])
            for _, row in df_chunk.iterrows()
            if row['text'] is not None and row['text'].strip() != ""
        ]
                
        # Initialize OpenSearch vector search client
        docsearch = OpenSearchVectorSearch.from_documents(
            documents,
            CustomEmbeddingFunction(),
            opensearch_url='vpc-ks-dev-opensearch-es-oacgyoijjstnydxq2itjbftyvm.us-west-2.es.amazonaws.com:443',
            http_auth=('ks-stg-admin', 'K3!0dg_7Hc'),
            timeout=900,
            use_ssl=True,
            verify_certs=False,
            ssl_assert_hostname=False,
            ssl_show_warn=False,
            index_name="kaas-ph2-2",
            engine="Lucene",
            method="hnsw",
            space_type="l2",
            bulk_size=10000
        )
        
        return True  # Return success status after uploading the chunk
    except Exception as e:
        print(f"Error processing chunk: {e}")
        return False  # Return failure status if an error occurs

# Main function to handle parallel processing
def send_to_opensearch_parallel(df, max_workers=10, chunk_size=500):
    # Split the DataFrame into chunks
    chunks = [df[i:i + chunk_size] for i in range(0, len(df), chunk_size)]
    
    # Use ThreadPoolExecutor to parallelize the operation
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        futures = {executor.submit(send_chunk_to_opensearch, chunk): chunk for chunk in chunks}
        
        # Collect results as they complete
        for future in as_completed(futures):
            chunk_id = futures[future]
            success = future.result()
            if success:
                print(f"Chunk {chunk_id} processed successfully")
            else:
                print(f"Chunk {chunk_id} processing failed")

# Example usage
# send_to_opensearch_parallel(df_result, max_workers=10, chunk_size=200)


In [40]:
# send to opensearch
from langchain.schema import Document
import os
from typing import List
import pymupdf4llm
from chromadb import EmbeddingFunction, Documents
from langchain.vectorstores import elasticsearch
#from chromadb import EmbeddingFunction, Documents, Embeddings
from langchain_community.document_loaders import PyPDFLoader
from langchain_community.retrievers import ElasticSearchBM25Retriever
from langchain_community.vectorstores import OpenSearchVectorSearch, Chroma
from langchain_text_splitters import MarkdownHeaderTextSplitter
from openai import OpenAI
import requests
from typing import List
from langchain_core.embeddings import Embeddings

def generate_embeddings(text):
    # Make sure to `pip install openai` first
    client = OpenAI(base_url="http://15.43.5.213:11434/v1", api_key="ollama")
    model="nomic-embed-text:latest"
    text = text.replace("\n", " ")
    return client.embeddings.create(input=[text], model=model).data[0].embedding

class CustomEmbeddingFunction(EmbeddingFunction):
    def __call__(self, texts: Documents) -> Embeddings:
        return list(map(generate_embeddings, texts))

    def embed_query(self, query: str) -> List[float]:
        return generate_embeddings(query)

    def embed_documents(self, texts: Documents) -> Embeddings:
        return list(map(generate_embeddings, texts))

def send_to_Opensearch(df):
    # Create Document objects from the DataFrame
    documents = [
        Document(page_content=row['text'], metadata=row['metadata'])
        for _, row in df.iterrows()
    ]
    
    docsearch = OpenSearchVectorSearch.from_documents(
        documents,
        CustomEmbeddingFunction(),
        opensearch_url='vpc-ks-dev-opensearch-es-oacgyoijjstnydxq2itjbftyvm.us-west-2.es.amazonaws.com:443',
        http_auth=('ks-stg-admin', 'K3!0dg_7Hc'),
        timeout=900,
        use_ssl=True,
        verify_certs=False,
        ssl_assert_hostname=False,
        ssl_show_warn=False,
        index_name="kaas-ph2-2",
        engine="Lucene",
        method="hnsw",
        space_type="l2",
        bulk_size=10000
    )

# Example of using the function with your DataFrame
# Assuming df is your DataFrame with 'page_content' and 'metadata' columns

In [53]:
# bulk render code
def get_bulk_render_url(documentIDs):
    
    bulk_render_url='https://css.api.hp.com/knowledge/v2/getRenderLinks'
    access_token = get_access_token()

    
    headers = {
        "Content-Type": "application/json",
        "Authorization": "Bearer " + access_token,
    }
    
    data = {
        "languageCode": 'en',
        "requests": [
            {
                "languageCode": 'en',
                "ids": documentIDs,
            },
        ],
    }
    
    response = requests.post(
        bulk_render_url, headers=headers, json=data
    )
    response.raise_for_status()
    response = response.json()
    data=response[0]['renderLinks']
    # print(data[0])
    # renderlinks = [i['renderLink'] for i in data if 'renderLink' in i]
    failed_count = sum(1 for i in data if i.get('status') == 'FAILURE')
    success_count = sum(1 for i in data if i.get('status') == 'SUCCESS')
    print(success_count,failed_count)
    return data
get_bulk_render_url(l)

573 27


[{'id': 'ish_9120060-9120054-16',
  'languageCode': 'en-US',
  'renderLink': 'https://css.api.hp.com/knowledge/v2/render/6f9MBfc6mzTcAhq2Kbx+Sy8tv9Hvi4fIarpLjO3hb3Q_hEJqA_dSTf48NoctmBGAobq52ZCGK3SZtmPHYBNAYa+q9ozEQtOdq9l6Xugo6Cj7of1BG1QLRIg0HG559CAjr7Dm2K6xTdlcMscvXv45DVk5pF6aLHiIPOo1xE88yfB+XnP4lImwlyVoZqZ1VjqtCqC_rhjsghIE_gxFTxaxWhF3mZY+1Hkno66EQm8V4wB0p+eTYgioP_aY4KpKcnPWigGCj2f6eZ6lDarptT784s8mjeewtsMv3XOmK_L_RNbuLhSkHu+pEKddViEgNaX23znzDYtAPfR2ZN2uDhKkxjNzwqbRJ3X2i_dds4WZXH+HtEpFfZreG3A_S4nWCBIYTo8MyOy02ZCYz49XiocoZz8erb_lYo5c33pJOx9HDJ0YxY_MxteHOEgOMQq3PU8mmCFrAdyyody6UKX8RvCBA7SEy+zVQEeqfVkY9a+JXhaYA9zAFreuVC1WS1WMgtoukV4uQgu_T1HQVMT6c4q8aeg1Au1UFJcHVyGH19nbycBIG8ADjlx7WMpxnSmofKpVY86DNDUEaiI8QOCdQubmZ9j+ZxSjdOO_EofDvJY6bsm3SP7lJ1YRMTXUWqHUfDPXNK17jlyhqzwFDQKGLe4VhgY77T70jAQukHZsdkFGehsuyA4xCYFi3OPaMiOgHaBcR7UIJyOCC1FePBIl7eqfYAe6BHiSRFL6l1lUwg1Ds8jS5kAOzL_nNefCUSnxCdne5ZMdOlCgY_mPpcJVmia3lNkq0xXV5gVvPgYQA9x3CNNhKgV+1kRYIE8TErvUrPXGsa9dd5rC4MSo4SIrb99VMn2gnsTe0IuJCmHYBzdutvtHtCf

In [15]:
pdf_documets=df1[df1['documentID'].apply(lambda x: x.startswith('pdf'))]
ish_documets=df1[df1['documentID'].apply(lambda x: x.startswith('ish'))]


In [ ]:
def clean_text(text):
    return ' '.join(text.split())

# Function to recursively extract text from paragraphs and headlines
def extract_content(soup):
    content = []
    for tag in soup.find_all(['p', 'h1', 'h2', 'h3', 'h4', 'h5', 'h6']):
        text = clean_text(tag.get_text())
        if text:
            content.append(text)
    return content

# Function to fetch and parse content for a given record (row from DataFrame)
def fetch_document_content(row):
    try:
        doc_id = row['documentID']  # Extract documentID from the row
        url = get_encrypted_token(doc_id)  # Fetch the URL using the encrypted token
        page = requests.get(url)  # Retrieve the page content
        html_content = page.content  # Directly store the HTML content in memory
        
        # Parse the HTML content using BeautifulSoup
        soup = BeautifulSoup(html_content, 'html.parser')
        
        # Extract text from paragraphs, headlines, etc.
        content = extract_content(soup)
        
        # Clean the extracted data
        all_content = '\n'.join(content)
        
        # Return the document metadata and content
        return {'metadata': row.to_dict(), 'text': all_content}
    except Exception as e:
        print(f"Error processing document ID {row['documentID']}: {e}")
        return {'metadata': row.to_dict(), 'text': None}

# Function to run multithreading and gather results
def process_documents_in_parallel(df, max_workers=10):
    data = []
    
    # Use ThreadPoolExecutor for parallel processing
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        # Submit tasks to the executor for each row in the DataFrame
        futures = {executor.submit(fetch_document_content, row): row['documentID'] for _, row in df.iterrows()}
        
        # Gather results as they are completed
        for future in as_completed(futures):
            result = future.result()
            if result:
                data.append(result)
    
    return data

# Process documents in parallel
data = process_documents_in_parallel(df1, max_workers=20)

# Create a new DataFrame from the collected data with 'metadata' and 'text' columns
df_result = pd.DataFrame(data)

In [61]:
def extract_cleaned_content(soup):
    content = []
    for tag in soup.find_all(['p', 'h1', 'h2', 'h3', 'h4', 'h5', 'h6']):
        text = ' '.join(tag.get_text().split())  # Clean and extract text in one step
        if text:
            content.append(text)
    return content

In [49]:
# parallel processing ish documents

from concurrent.futures import ThreadPoolExecutor, as_completed
import requests
from bs4 import BeautifulSoup

def get_bulk_render_url(documentIDs):
    
    bulk_render_url='https://css.api.hp.com/knowledge/v2/getRenderLinks'
    access_token = get_access_token()
        
    headers = {
        "Content-Type": "application/json",
        "Authorization": "Bearer " + access_token,
    }
    
    data = {
        "languageCode": 'en',
        "requests": [
            {
                "languageCode": 'en',
                "ids": documentIDs,
            },
        ],
    }
    
    response = requests.post(
        bulk_render_url, headers=headers, json=data
    )
    response.raise_for_status()
    response = response.json()
    data=response[0]['renderLinks']
    # print(data[0])
    renderlinks = [i['renderLink'] for i in data if 'renderLink' in i]
    failed_count = sum(1 for i in data if i.get('status') == 'FAILURE')
    success_count = sum(1 for i in data if i.get('status') == 'SUCCESS')
    # print(success_count,failed_count)
    return renderlinks

# Function to fetch and process content from each document in the batch
def fetch_and_process_document_content(url, row):
    try:
        page = requests.get(url)  # Retrieve the page content
        html_content = page.content  # Directly store the HTML content in memory
        
        # Parse the HTML content using BeautifulSoup
        soup = BeautifulSoup(html_content, 'html.parser')
        
        # Extract and clean text from paragraphs, headlines, etc.
        content = extract_cleaned_content(soup)
        all_content = '\n'.join(content)
        
        # Return the document metadata and content
        return {'metadata': row.to_dict(), 'text': all_content}
    except Exception as e:
        print(f"Error processing document from URL {url}: {e}")
        return {'metadata': row.to_dict(), 'text': None}

# Function to process a batch of documents
def process_batch(batch_rows):
    # Check if batch_rows is a DataFrame, and if so, iterate using .iterrows()
    if isinstance(batch_rows, pd.DataFrame):
        batch_rows = [row for _, row in batch_rows.iterrows()]  # Convert rows to list of Series
    
    # Now batch_rows is a list of rows (Series or dict-like), safe to extract 'documentID'
    document_ids = [row['documentID'] for row in batch_rows]

    # Fetch URLs for the batch of document IDs
    urls = get_bulk_render_url(document_ids)  # Assuming this is the updated function for bulk URL fetching

    # Use a thread pool to fetch and process each document's content in parallel
    results = []
    with ThreadPoolExecutor(max_workers=len(batch_rows)) as executor:
        futures = {
            executor.submit(fetch_and_process_document_content, url, row): row['documentID'] 
            for url, row in zip(urls, batch_rows)
        }
        
        for future in as_completed(futures):
            result = future.result()
            if result:
                results.append(result)
    
    return results

# Function to split DataFrame into batches and process them in parallel
def process_documents_in_parallel(df, batch_size=500, max_workers=10):
    data = []
    
    # Split the DataFrame into batches of `batch_size`
    batches = [df[i:i + batch_size] for i in range(0, len(df), batch_size)]
    
    # Process batches in parallel using ThreadPoolExecutor
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        futures = [executor.submit(process_batch, batch) for batch in batches]
        
        for future in as_completed(futures):
            batch_results = future.result()
            data.extend(batch_results)
    
    return data

# Process documents in parallel
data = process_documents_in_parallel(ish_documets, batch_size=500, max_workers=20)
ish_df=pd.DataFrame(data)

Error processing document from URL https://css.api.hp.com/knowledge/v2/render/6f9MBfczkDLVDB62Kbp7Ti4gvtHvi4fIarpLjO3hb3Q_hEJqA_dSTf48NoctmBGAobq52ZCGK3SZtmPHYBNAYa+q9ozEQtOdq9l6Xugo6Cj7of1BG1QLRIg0HG559CAjr7Dm2K6xTdlcMscvXv45DVk5pF6aLHiIPOo1xE88yfB+XnP4lImwlyVoZqZ1VjqtCqC_rhjsghIE_gxFTxaxWhF3mZY+1Hkno66EQm8V4wB0p+eTYgioP_aY4KpKcnPWigGCj2f6eZ6lDarptT784s8mjeewtsMv3XOmK_L_RNbuLhSkHu+pEKddViEgNaX23znzDYtAPfR2ZN2uDhKkxjNzwqbRJ3X2i_dds4WZXH+HtEpFfZreG3A_S4nWCBIYTo8MyOy02ZCYz49XiocoZz8erb_lYo5c33pJOx9HDJ0YxY_MxteHOEgOMQq3PU8mmCFrAdyyody6UKX8RvCBA7SEy+zVQEeqfVkY9a+JXhaYA9zAFreuVC1WS1WMgtoukV4uQgu_T1HQVMT6c4q8aeg1Au1UFJcHVyGH19nbycBIG8ADjlx7WMpxnSmofKpVY86DNDUEaiI8QOCdQubmZ9j+ZxSjdOO_EofDvagiacqJUPPlJ1YRMTXUWqHUfDPXNK18jXK5pj8rGQKGLe4VhgY77T70jAQukHZsdkFGehsuyA4xCYFi3OPaMiOgHaBcR7UIJyOCC1FePBIl7eqfYAe6BHiSRFL6l1lUwg1Ds8jS5kAOzL_nNefBDT3fCZvJg5xELVCjPPifqppCtzK2lNky0xXV5gVtEDQSAtx3CNNPKgZ96FwVIV8HErvUrPXGhJJLQYb51pW5vGZpXaFSEFqGo4b9pq6MBBqDBgo8vqhmvg2JGqkDCYYFiS5LumChW4Z0nS9JJUVoLF4Dlew8qxJn3Z

In [51]:
len(data)
ish_df.shape

4273

(4273, 2)

In [24]:
# pdf documents
import requests
from io import BytesIO
from PyPDF2 import PdfReader
import pandas as pd
from multiprocessing import Pool, cpu_count
def split_Page1(url):
    try:
        # Download the file from the provided URL
        response = requests.get(url)
        
        # Check if the request was successful
        if response.status_code == 200:
            # Load the PDF content using BytesIO
            file_stream = BytesIO(response.content)
            
            try:
                # Attempt to load and process the PDF using PyPDF2
                reader = PdfReader(file_stream)
                pages = [page.extract_text() for page in reader.pages]
                return pages
            except Exception as pdf_error:
                print(f"Failed to process the file as a PDF: {pdf_error}")
                return None
        else:
            print(f"Failed to fetch URL: {url}")
            return None
    except Exception as e:
        print(f"Error processing URL: {url}. Error: {e}")
        return None

def get_bulk_renderlink(documentIDs):
    
    bulk_render_url='https://css.api.hp.com/knowledge/v2/getRenderLinks'
    access_token = get_access_token()
        
    headers = {
        "Content-Type": "application/json",
        "Authorization": "Bearer " + access_token,
    }
    
    data = {
        "languageCode": 'en',
        "requests": [
            {
                "languageCode": 'en',
                "ids": documentIDs,
            },
        ],
    }
    
    response = requests.post(
        bulk_render_url, headers=headers, json=data
    )
    response.raise_for_status()
    response = response.json()
    data=response[0]['renderLinks']
    # print(data[0])
    renderlinks = {i['id']:i['renderLink'] for i in data if 'renderLink' in i}

    return renderlinks

def preprocessing(df, doc_id_column='documentID', batch_size=500):
    # List to hold records
    records = []
    
    # Break document IDs into batches of 500
    document_id_batches = [df[doc_id_column].iloc[i:i+batch_size] for i in range(0, len(df), batch_size)]
    
    # Iterate over each batch of document IDs
    for batch in document_id_batches:
        # Get the URLs for the current batch of document IDs
        document_ids = batch.tolist()
        url_mapping = get_bulk_renderlink(document_ids)
        
        # Iterate over the document IDs and URLs
        for doc_id in document_ids:
            # Extract the corresponding URL
            url = url_mapping.get(doc_id)
            
            # Extract pages from the URL
            if url:
                pages = split_Page1(url)
                
                # Continue if pages were successfully extracted
                if pages is not None:
                    # Create metadata dictionary from other columns
                    row = df[df[doc_id_column] == doc_id].iloc[0]
                    metadata = row.to_dict()
                    
                    # Create a record for each page
                    for page_num, page in enumerate(pages, start=1):
                        # Add page number to the metadata
                        meta_with_page_num = metadata.copy()
                        meta_with_page_num['page_number'] = page_num
                        
                        # Append the record to the list
                        records.append({
                            'metadata': meta_with_page_num,
                            'page_text': page
                        })
    
    # Return a new DataFrame with separate records for each page
    return pd.DataFrame(records)


In [25]:
dfp=preprocessing(pdf_documets)

Failed to fetch URL: https://kaas.hpcloud.hp.com/pdf-nonpublic/pdf_3999714_en-US-6.pdf?Expires=1727808067&Signature=ebgqU2OsmcHa8i60P7amC8oD27pJ2oI~uzlHz1AT645AWtcfgtowh8GUe8zPT6FC~1SJ-JQ84KqCKVHs4Ukjgm-pP7BAjlgjAHdDyHpwIrfqCvy3mY4KdSS50EZ7PDloLeZBBqU7kZ1blZq~aYH4Zfcjndeu8vUxBJERUmuwNxRBfmuV14FXPs5BXM4gU~WpfqbPceATgnbukdQGOMWRsg0GU3AQ2cvdBDq7gOV90ieJbWiTA4yqI3FjymANKoU~TxqRdHDg-CLUZskpcjs2uX7CtIuEC-2wjS5KMztNiSsitVNEhfmGgqfuZhe7cZ~Bq0D6q5f0YtAMxhhGEAQyJQ__&Key-Pair-Id=APKAIEP4ZT2OPKULVJXQ


unknown widths : 
[0, IndirectObject(257, 0, 1962357210384)]
unknown widths : 
[0, IndirectObject(265, 0, 1962357210384)]
unknown widths : 
[0, IndirectObject(261, 0, 1962357210384)]


In [27]:
dfp.rename(columns={'page_text':'text'},inplace=True)
dfp1=dfp[dfp['text'].apply(lambda x: len(x)>1)]

2024-10-01 22:02:52.842855


In [45]:
print(datetime.datetime.now())
send_to_opensearch_parallel(dfp1[500:], max_workers=10, chunk_size=100)

2024-10-01 22:03:02.596904
Chunk                                                metadata  \
1989  {'documentID': 'pdf_10744739_en-US-6', 'title'...   
1990  {'documentID': 'pdf_10744739_en-US-6', 'title'...   
1991  {'documentID': 'pdf_10744739_en-US-6', 'title'...   
1992  {'documentID': 'pdf_10744739_en-US-6', 'title'...   
1993  {'documentID': 'pdf_10744739_en-US-6', 'title'...   
...                                                 ...   
2084  {'documentID': 'pdf_9090144_en-US-6', 'title':...   
2085  {'documentID': 'pdf_9090144_en-US-6', 'title':...   
2086  {'documentID': 'pdf_9090144_en-US-6', 'title':...   
2087  {'documentID': 'pdf_9090144_en-US-6', 'title':...   
2088  {'documentID': 'pdf_9090144_en-US-6', 'title':...   

                                                   text  
1989  10. The upper screw on the right bracket of ea...  
1990  Using the PITC heater\nThis section is only re...  
1991  2. Replace the valve.\nServicing the economize...  
1992  1. Change the press 

In [46]:
print(datetime.datetime.now())

2024-10-01 22:52:26.290571


In [35]:
send_to_Opensearch(dfp[:2])

In [31]:
dfp.iloc[:2]

metadata  \
0  {'title': 'HP Indigo Tips and Tricks CA494–076...   
1  {'title': 'HP Indigo Tips and Tricks CA494–076...   

                                           page_text  
0  HP Indigo Tips and Tricks CA494–07671 — April ...  
1  Category Known issue/Tip Tips and Tricks\nBlan...

In [48]:
dfp1.shape

(22250, 2)